In [1]:
import os
import json
# import time
os.environ["NCCL_P2P_DISABLE"] = "1"
import torch 
# import pynvml
from vllm import LLM, SamplingParams
import torch.distributed as dist
import re
torch.cuda.empty_cache()
os.environ["TRANSFORMERS_OFFLINE"] = "1"
os.environ["HF_DATASETS_OFFLINE"] = "1"
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"



# 加载量化模型
llm = LLM(model="/opt/lung/llm/Qwen/Qwen2.5-Coder-14B-Instruct-GPTQ-Int8", dtype="half",gpu_memory_utilization=0.9)

# 
sampling_params = SamplingParams(temperature=0.1, top_p=0.3, max_tokens = 256)

# 推理示例


/home/limeng/anaconda3/envs/Qwen2.5/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2025-03-19 13:23:29,599	INFO util.py:154 -- Missing packages: ['ipywidgets']. Run `pip install -U ipywidgets`, then restart the notebook server for rich notebook output.


INFO 03-19 13:23:37 config.py:350] This model supports multiple tasks: {'generate', 'embedding'}. Defaulting to 'generate'.
WARNING 03-19 13:23:37 config.py:428] gptq quantization is not fully optimized yet. The speed can be slower than non-quantized models.
INFO 03-19 13:23:37 llm_engine.py:249] Initializing an LLM engine (v0.6.4.post1) with config: model='/opt/lung/llm/Qwen/Qwen2.5-Coder-14B-Instruct-GPTQ-Int8', speculative_config=None, tokenizer='/opt/lung/llm/Qwen/Qwen2.5-Coder-14B-Instruct-GPTQ-Int8', skip_tokenizer_init=False, tokenizer_mode=auto, revision=None, override_neuron_config=None, tokenizer_revision=None, trust_remote_code=False, dtype=torch.float16, max_seq_len=32768, download_dir=None, load_format=LoadFormat.AUTO, tensor_parallel_size=1, pipeline_parallel_size=1, disable_custom_all_reduce=False, quantization=gptq, enforce_eager=False, kv_cache_dtype=auto, quantization_param_path=None, device_config=cuda, decoding_config=DecodingConfig(guided_decoding_backend='outlines

[W319 13:23:39.079105545 CUDAAllocatorConfig.h:28] Warning: expandable_segments not supported on this platform (function operator())
Loading safetensors checkpoint shards:   0% Completed | 0/5 [00:00<?, ?it/s]
Loading safetensors checkpoint shards:  20% Completed | 1/5 [00:10<00:40, 10.09s/it]
Loading safetensors checkpoint shards:  40% Completed | 2/5 [00:11<00:15,  5.20s/it]
Loading safetensors checkpoint shards:  60% Completed | 3/5 [00:38<00:30, 15.17s/it]
Loading safetensors checkpoint shards:  80% Completed | 4/5 [00:43<00:10, 10.93s/it]
Loading safetensors checkpoint shards: 100% Completed | 5/5 [00:46<00:00,  8.23s/it]
Loading safetensors checkpoint shards: 100% Completed | 5/5 [00:46<00:00,  9.35s/it]



INFO 03-19 13:24:27 model_runner.py:1077] Loading model weights took 15.5028 GB
INFO 03-19 13:24:38 worker.py:232] Memory profiling results: total_gpu_memory=31.73GiB initial_memory_usage=15.89GiB peak_torch_memory=19.42GiB memory_usage_post_profile=15.96GiB non_torch_memory=0.45GiB kv_cache_size=8.69GiB gpu_memory_utilization=0.90
INFO 03-19 13:24:38 gpu_executor.py:113] # GPU blocks: 2965, # CPU blocks: 1365
INFO 03-19 13:24:38 gpu_executor.py:117] Maximum concurrency for 32768 tokens per request: 1.45x
INFO 03-19 13:24:42 model_runner.py:1400] Capturing cudagraphs for decoding. This may lead to unexpected consequences if the model is not static. To run the model in eager mode, set 'enforce_eager=True' or use '--enforce-eager' in the CLI.
INFO 03-19 13:24:42 model_runner.py:1404] If out-of-memory error occurs during cudagraph capture, consider decreasing `gpu_memory_utilization` or switching to eager mode. You can also reduce the `max_num_seqs` as needed to decrease memory usage.
INF

In [2]:
import pandas as pd 

df = pd.read_csv('/home/limeng/SICT/lung_test/result/喉癌患者测试样例_完整字段_tfidf_match.csv',encoding='gb2312')
df = df
df

Id PatientName    IPBLH  OPBLH                KH  KLX  SexId  \
0     507444          林*  1559494    NaN        9948848999    3      2   
1     507444          林*  1559494    NaN        9948848999    3      2   
2     507444          林*  1559494    NaN        9948848999    3      2   
3     507444          林*  1559494    NaN        9948848999    3      2   
4     507444          林*  1559494    NaN        9948848999    3      2   
..       ...         ...      ...    ...               ...  ...    ...   
122  1571219          张*  1615739    NaN  167313826_320500    4      2   
123  1571219          张*  1615739    NaN  167313826_320500    4      2   
124  1571219          张*  1615739    NaN  167313826_320500    4      2   
125  1571219          张*  1615739    NaN  167313826_320500    4      2   
126  1571219          张*  1615739    NaN  167313826_320500    4      2   

           CSRQ  ZJLX                SFZH  ...  ValueString  \
0     2002/10/2     1  377474********0222  ...           测试   
1     2002/10/2     1  377474********0222  ...            女   
2     2002/10/2     1  377474********0222  ...          22岁   
3     2002/10/2     1  377474********0222  ...    发生发放安抚啊医院   
4     2002/10/2     1  377474********0222  ...  6.38528E+17   
..          ...   ...                 ...  ...          ...   
122  1994/10/23     1  350301********2829  ...           Ib   
123  1994/10/23     1  350301********2829  ...            右   
124  1994/10/23     1  350301********2829  ...           Ia   
125  1994/10/23     1  350301********2829  ...          NaN   
126  1994/10/23     1  350301********2829  ...  6.38712E+17   

          DisplayString  ValuePostfix          WSJLSCSJ          WSJLXGSJ  \
0                    测试           NaN  2024/11/28 14:08  2024/11/28 14:09   
1                     女           NaN  2024/11/28 14:08  2024/11/28 14:09   
2                   22岁           NaN  2024/11/28 14:08  2024/11/28 14:09   
3             发生发放安抚啊医院           NaN  2024/11/28 14:08  2024/11/28 14:09   
4     2024年05月31日20时56分       收入我科入院。  2024/11/28 14:08  2024/11/28 14:09   
..                  ...           ...               ...               ...   
122                  Ib           NaN  2024/12/30 17:18  2024/12/30 17:23   
123                   右           NaN  2024/12/30 17:18  2024/12/30 17:23   
124                  Ia           NaN  2024/12/30 17:18  2024/12/30 17:23   
125                               NaN  2024/12/30 17:18  2024/12/30 17:23   
126  2024年12月30日 17时11分           NaN  2024/12/30 17:18  2024/12/30 17:23   

        upload_time                     规范节点名        规范注释  规范说明  \
0    2025/2/8 12:05      COC_HBZL_RYJLFL$hzxm        患者姓名   NaN   
1    2025/2/8 12:05      COC_HBZL_RYJLFL$hzxb        患者性别   NaN   
2    2025/2/8 12:05      COC_HBZL_RYJLFL$hznl        患者年龄   NaN   
3    2025/2/8 12:05          COC_HBZL_RYJL$zs          主诉   NaN   
4    2025/2/8 12:05  COC_HBZL_CYXJ$rysqk_rysj  入院时情况-入院时间   NaN   
..              ...                       ...         ...   ...   
122  2025/2/8 12:05        COC_HBZL_SSJL$ssjg        手术经过   NaN   
123  2025/2/8 12:05        COC_HBZL_SSJL$ssjg        手术经过   NaN   
124  2025/2/8 12:05        COC_HBZL_SSJL$ssjg        手术经过   NaN   
125  2025/2/8 12:05        COC_HBZL_SSJL$zdys        主刀医师   NaN   
126  2025/2/8 12:05        COC_HBZL_SSJL$zdys        主刀医师   NaN   

       processed_string  
0                    测试  
1                     女  
2                   22岁  
3             发生发放安抚啊医院  
4     2024年05月31日20时56分  
..                  ...  
122                  Ib  
123                   右  
124                  Ia  
125                      
126  2024年12月30日 17时11分  

[127 rows x 54 columns]

In [5]:
df['规范说明']

0      NaN
1      NaN
2      NaN
3      NaN
4      NaN
      ... 
122    NaN
123    NaN
124    NaN
125    NaN
126    NaN
Name: 规范说明, Length: 127, dtype: object

In [6]:
result = []
for valueitemname,displaystring,expla in zip(df.ValueItemName,df.DisplayString,df['规范说明']):
    print(valueitemname,displaystring,expla)

    prompt = f"""
你是一个专业的数据处理助手。你的任务是根据给定的规范说明处理输入的字符串值。

请遵循以下规则：
1. 如果提供了规范说明（非null），并且输入字符串可以映射到规范中的某个选项，则将字符串替换为对应的选项编号
2. 如果规范说明为null或输入字符串无法映射到规范中的任何选项，则保持字符串不变
3. 你必须以JSON格式返回结果，包含三个字段：
   - "original_string": 原始输入的字符串
   - "standard_description": 规范说明（如果为null则保持为null）
   - "processed_string": 处理后的字符串

示例1：
输入：
字符串："精神尚可"
规范说明："1: 良好 2:一般 3:较差 4:很差"

输出：
{{
  "original_string": "神志状态",
  "standard_description": "1: 良好 2:一般 3:较差 4:很差",
  "processed_string": "1"

}}

示例2：
输入：
字符串："体温"
规范说明：null

输出：
{
 { "original_string": "体温",
  "standard_description": "null",
  "processed_string": "体温"}
}

示例3：
输入：
字符串："血压"
规范说明："1:正常 2:偏高 3:偏低"

输出：
{
  {"original_string": "血压",
  "standard_description": "1:正常 2:偏高 3:偏低",
  "processed_string": "血压"}
}

现在，请处理以下输入：
字符串：{displaystring}
规范说明：{expla}
"""
    output = llm.generate(prompt, sampling_params)
    print(output[0].outputs[0].text)
    try:
        match = re.search(r'```json\n(.*?)\n```', output[0].outputs[0].text, re.DOTALL)
        if match:
            # print(match.group(1))
            result.append(json.loads(match.group(1)))
    except Exception as e:
        print(f"解析出错: {e}")
        result.append(output[0].outputs[0].text)

病人姓名 测试 nan


Processed prompts: 100%|██████████| 1/1 [00:01<00:00,  1.00s/it, est. speed input: 333.99 toks/s, output: 30.91 toks/s]


```json
{
  "original_string": "测试",
  "standard_description": "nan",
  "processed_string": "测试"
}
```
性别 女 nan


Processed prompts: 100%|██████████| 1/1 [00:00<00:00,  1.23it/s, est. speed input: 411.50 toks/s, output: 38.08 toks/s]


```json
{
  "original_string": "女",
  "standard_description": "nan",
  "processed_string": "女"
}
```
年龄 22岁 nan


...

```json
{
  "original_string": "Ia",
  "standard_description": "nan",
  "processed_string": "Ia"
}
```
记录医师   nan


Processed prompts: 100%|██████████| 1/1 [00:01<00:00,  1.14s/it, est. speed input: 294.54 toks/s, output: 23.81 toks/s]


```json
{
  "original_string": "",
  "standard_description": "nan",
  "processed_string": ""
}
```
记录时间 2024年12月30日 17时11分 nan


Processed prompts: 100%|██████████| 1/1 [00:02<00:00,  2.33s/it, est. speed input: 151.36 toks/s, output: 27.95 toks/s]

```json
{
  "original_string": "2024年12月30日 17时11分",
  "standard_description": "nan",
  "processed_string": "2024年12月30日 17时11分"
}
```


In [7]:
result
print(len(result))

127


In [8]:
string_result = [] 
for data in result:
    string_result.append(data['processed_string'])
string_result

['测试',
 '女',
 '22岁',
 '发生发放安抚啊医院',
 '2024年05月31日20时56分',
 '神志清',
 '1',
 '食欲如常',
 '1',
 '1',
 '1',
 '体重无明显变化',
 '1',
 '可',
 '1',
 '1',
 '呼吸平稳',
 '1',
 '1',
 '0',
 '1',
 '0',
 '0',
 '清',
 '对称',
 '0',
 '0',
 '齐',
 '未闻及',
 '0',
 '0',
 '0',
 '0',
 '自如',
 '1',
 '0',
 '发生发放安抚啊医院',
 '王丽君',
 '2024/11/28',
 '张**',
 '男',
 '2024/12/6 11:30',
 '2024/12/6 11:58',
 '声带病损切除术',
 '陈东',
 '全身麻醉',
 '左声带全长白斑样新生物',
 '',
 '2024年12月06日 18时17分',
 '朱**',
 '男',
 '73岁',
 '3589276',
 '2024/12/3 09:22',
 '2024/12/9 16:00',
 '声嘶3月余',
 '1周',
 '盐酸克林霉素棕榈酸酯分散片 150mg*6片/盒 150mg 口服 Tid  (共：2盒)',
 '',
 '',
 '孙会猛',
 '朱**',
 '男',
 '2024/12/5 13:15',
 '2024/12/5 14:13',
 '喉部分切除术',
 '王振涛',
 '周杰玉',
 '谭皓月',
 '全身麻醉',
 '切取部分肿物送冰冻，提示（左声带肿物）高级别鳞状上皮内瘤变，疑有癌变。告知家属病情，拟行支撑喉镜下垂直半喉切除术。',
 '',
 '2024年12月05日 15时04分',
 '顾**',
 '男',
 '2024/12/13 13:30',
 '2024/12/13 16:05',
 '喉部分切除术',
 '王振涛',
 '全身麻醉',
 '',
 '2024年12月18日 15时36分',
 '陈**',
 '男',
 '2024/12/3 13:15',
 '2024/12/3 15:43',
 '喉部分切除术',
 '王家东',
 '薛娜',
 '薛璐',
 '全身麻醉',
 '颈前“U”切口，并翻“U”颈阔肌瓣',

In [10]:
df['processed_string'] = string_result
df


Id PatientName    IPBLH  OPBLH                KH  KLX  SexId  \
0     507444          林*  1559494    NaN        9948848999    3      2   
1     507444          林*  1559494    NaN        9948848999    3      2   
2     507444          林*  1559494    NaN        9948848999    3      2   
3     507444          林*  1559494    NaN        9948848999    3      2   
4     507444          林*  1559494    NaN        9948848999    3      2   
..       ...         ...      ...    ...               ...  ...    ...   
122  1571219          张*  1615739    NaN  167313826_320500    4      2   
123  1571219          张*  1615739    NaN  167313826_320500    4      2   
124  1571219          张*  1615739    NaN  167313826_320500    4      2   
125  1571219          张*  1615739    NaN  167313826_320500    4      2   
126  1571219          张*  1615739    NaN  167313826_320500    4      2   

           CSRQ  ZJLX                SFZH  ...  ValueString  \
0     2002/10/2     1  377474********0222  ...           测试   
1     2002/10/2     1  377474********0222  ...            女   
2     2002/10/2     1  377474********0222  ...          22岁   
3     2002/10/2     1  377474********0222  ...    发生发放安抚啊医院   
4     2002/10/2     1  377474********0222  ...  6.38528E+17   
..          ...   ...                 ...  ...          ...   
122  1994/10/23     1  350301********2829  ...           Ib   
123  1994/10/23     1  350301********2829  ...            右   
124  1994/10/23     1  350301********2829  ...           Ia   
125  1994/10/23     1  350301********2829  ...          NaN   
126  1994/10/23     1  350301********2829  ...  6.38712E+17   

          DisplayString  ValuePostfix          WSJLSCSJ          WSJLXGSJ  \
0                    测试           NaN  2024/11/28 14:08  2024/11/28 14:09   
1                     女           NaN  2024/11/28 14:08  2024/11/28 14:09   
2                   22岁           NaN  2024/11/28 14:08  2024/11/28 14:09   
3             发生发放安抚啊医院           NaN  2024/11/28 14:08  2024/11/28 14:09   
4     2024年05月31日20时56分       收入我科入院。  2024/11/28 14:08  2024/11/28 14:09   
..                  ...           ...               ...               ...   
122                  Ib           NaN  2024/12/30 17:18  2024/12/30 17:23   
123                   右           NaN  2024/12/30 17:18  2024/12/30 17:23   
124                  Ia           NaN  2024/12/30 17:18  2024/12/30 17:23   
125                               NaN  2024/12/30 17:18  2024/12/30 17:23   
126  2024年12月30日 17时11分           NaN  2024/12/30 17:18  2024/12/30 17:23   

        upload_time                     规范节点名        规范注释  规范说明  \
0    2025/2/8 12:05      COC_HBZL_RYJLFL$hzxm        患者姓名   NaN   
1    2025/2/8 12:05      COC_HBZL_RYJLFL$hzxb        患者性别   NaN   
2    2025/2/8 12:05      COC_HBZL_RYJLFL$hznl        患者年龄   NaN   
3    2025/2/8 12:05          COC_HBZL_RYJL$zs          主诉   NaN   
4    2025/2/8 12:05  COC_HBZL_CYXJ$rysqk_rysj  入院时情况-入院时间   NaN   
..              ...                       ...         ...   ...   
122  2025/2/8 12:05        COC_HBZL_SSJL$ssjg        手术经过   NaN   
123  2025/2/8 12:05        COC_HBZL_SSJL$ssjg        手术经过   NaN   
124  2025/2/8 12:05        COC_HBZL_SSJL$ssjg        手术经过   NaN   
125  2025/2/8 12:05        COC_HBZL_SSJL$zdys        主刀医师   NaN   
126  2025/2/8 12:05        COC_HBZL_SSJL$zdys        主刀医师   NaN   

       processed_string  
0                    测试  
1                     女  
2                   22岁  
3             发生发放安抚啊医院  
4     2024年05月31日20时56分  
..                  ...  
122                  Ib  
123                   右  
124                  Ia  
125                      
126  2024年12月30日 17时11分  

[127 rows x 54 columns]

In [11]:
df.to_csv('/home/limeng/SICT/lung_test/result/reflected_result319.csv',encoding='gb2312',index=False)

In [21]:
import pymysql

# 连接到MySQL服务器（不指定数据库）
try:
    # 首先尝试连接到MySQL服务器（不指定数据库）
    conn = pymysql.connect(
       host='localhost',
       user='newuser',  # 或者您创建的新用户
       password='Sict@2024',  # 不是临时密码，而是您更改后的密码
       charset='utf8mb4',
       client_flag=pymysql.constants.CLIENT.MULTI_STATEMENTS  # 添加这一行允许多语句执行
   )
    print("成功连接到MySQL服务器")
    
    # 创建一个游标对象
    cursor = conn.cursor()
    
    cursor.execute("SHOW DATABASES LIKE 'target_db'")
    db_exists = cursor.fetchone()

    if db_exists:
        print("数据库 'target_db' 已存在，正在删除...")
        cursor.execute("DROP DATABASE target_db")
        print("数据库 'target_db' 已成功删除")
    # 创建新数据库
    cursor.execute("CREATE DATABASE IF NOT EXISTS target_db")
    print("数据库 'target_db' 创建成功或已存在")
    
    # 使用新创建的数据库
    cursor.execute("USE target_db")
    print("切换到数据库 'target_db'")
    
    # 执行 SQL 语句来创建表
    create_table_sql = """
     -- 喉癌_放疗小结
DROP TABLE IF EXISTS coc_zy_hbzl_flxj;
CREATE TABLE `coc_zy_hbzl_flxj` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `kh`  varchar(32)   NOT NULL  COMMENT "卡号（患者就诊卡卡号）",
  `klx`  varchar(16)   NOT NULL  COMMENT "卡类型（参见字典表）",
  `xgbz`  varchar(1)   NOT NULL  COMMENT "修改标志（1:正常 2:修改3:撤销）",
  `yjlxh`  varchar(32)   NOT NULL  COMMENT "原纪录序号（院内唯一标识）",
  `zlkssj`  varchar(20)   NULL  COMMENT "治疗开始日期",
  `zljssj`  varchar(20)   NULL  COMMENT "治疗结束日期",
  `zd`  varchar(100)   NULL  COMMENT "诊断",
  `ybqk_zyzzjtz_xm`  varchar(50)   NULL  COMMENT "一般情况-主要症状及体征-姓名",
  `ybqk_zyzzjtz_xb`  varchar(10)   NULL  COMMENT "一般情况-主要症状及体征-性别",
  `ybqk_zyzzjtz_nl`  varchar(10)   NULL  COMMENT "一般情况-主要症状及体征-年龄",
  `ybqk_zyzzjtz_zsms`  varchar(1000)   NULL  COMMENT "一般情况-主要症状及体征-主诉",
  `ybqk_zyzzjtz_ryzd`  varchar(100)   NULL  COMMENT "一般情况-主要症状及体征-入院诊断",
  `ybqk_zyzzjtz_ryrq`  varchar(20)   NULL  COMMENT "一般情况-主要症状及体征-入院日期",
  `ybqk_sg`  varchar(6)   NULL  COMMENT "一般情况-身高（Cm）",
  `ybqk_tz`  varchar(6)   NULL  COMMENT "一般情况-体重（Kg）",
  `ybqk_kpspf`  varchar(2)   NULL  COMMENT "一般情况-KPS评分（0:0分 1:10分，2:20分 3:30分4:40分5:50分 6:60分 7:70分 8:80分 9:90分10:100分）",
  `ybqk_xbs`  varchar(2000)   NULL  COMMENT "一般情况-现病史",
  `zyfzjc_blbg`  varchar(500)   NULL  COMMENT "主要辅助检查-病理报告",
  `zyfzjc_hbctmri`  varchar(500)   NULL  COMMENT "主要辅助检查-喉部CT,MR",
  `zyfzjc_sysjc_bxb`  varchar(100)   NULL  COMMENT "主要辅助检查-实验室检查-白细胞",
  `zyfzjc_sysjc_hxb`  varchar(100)   NULL  COMMENT "主要辅助检查-实验室检查-红细胞",
  `zyfzjc_sysjc_xxb`  varchar(100)   NULL  COMMENT "主要辅助检查-实验室检查-血小板",
  `zyfzjc_sysjc_gbzam`  varchar(100)   NULL  COMMENT "主要辅助检查-实验室检查-谷丙转氨酶",
  `zyfzjc_sysjc_gczam`  varchar(100)   NULL  COMMENT "主要辅助检查-实验室检查-谷草转氨酶",
  `zyfzjc_sysjc_rstqm`  varchar(100)   NULL  COMMENT "主要辅助检查-实验室检查-乳酸脱氢酶",
  `zyfzjc_sysjc_jlz`  varchar(100)   NULL  COMMENT "主要辅助检查-实验室检查-K",
  `zyfzjc_sysjc_nlz`  varchar(100)   NULL  COMMENT "主要辅助检查-实验室检查-Na",
  `zyfzjc_sysjc_llz`  varchar(100)   NULL  COMMENT "主要辅助检查-实验室检查-CL",
  `zljg_zlksrq`  varchar(20)   NULL  COMMENT "诊疗经过-治疗开始日期",
  `zljg_zljsrq`  varchar(20)   NULL  COMMENT "诊疗经过-治疗结束日期",
  `zljg_zlfs`  varchar(2)   NULL  COMMENT "诊疗经过-治疗方式（1:放疗 2:化疗3:靶向治疗 4:免疫治疗）",
  `zljg_jtfa`  varchar(1000)   NULL  COMMENT "诊疗经过-具体方案",
  `zljg_zlgc`  varchar(2)   NULL  COMMENT "诊疗经过-治疗过程（1:顺利 2:有异常情况）",
  `zljg_blfydj`  varchar(2)   NULL  COMMENT "诊疗经过-不良反应等级（1:1 2:2 3:3 4:4）",
  `zljg_blfylx`  varchar(2)   NULL  COMMENT "诊疗经过-不良反应类型（1:胃肠道反应 2:血液学毒性 3:口腔粘膜反应 4:皮肤毒性5:内分泌反应 6:肝毒性 7:心脏毒性）",
  `zljg_zlzt`  varchar(2)   NULL  COMMENT "诊疗经过-治疗状态（1:完成 2:暂停3:中止）",
  `zljg_zllx`  varchar(2)   NULL  COMMENT "诊疗经过-治疗类型（1:根治性放疗 2:同步放化疗 3:术前放疗 4:术后放疗 5:姑息性放疗 6:化疗 7:靶向治疗 8:免疫治疗）",
  `sfzdfl`  varchar(2)   NULL  COMMENT "中断放疗-是否（1:是  0:否）",
  `zdfl_zdyy`  varchar(2)   NULL  COMMENT "中断放疗-中断天数（0-50）",
  `zdfl_zdts`  varchar(100)   NULL  COMMENT "中断放疗-中断原因",
  `sftbhl`  varchar(2)   NULL  COMMENT "同步化疗-是否（1:是  0:否）",
  `tbhl_ym`  varchar(2)   NULL  COMMENT "同步化疗-药名（1:顺铂 2:奈达铂 3:卡铂）",
  `tbhl_jl`  varchar(4)   NULL  COMMENT "同步化疗-剂量（（10-300）mg/天）",
  `tbhl_ts`  varchar(2)   NULL  COMMENT "同步化疗-天数（（0-3）天）",
  `tbhl_yf`  varchar(2)   NULL  COMMENT "同步化疗-用法（1:ivgtt 2:po）",
  `tbhl_pc`  varchar(2)   NULL  COMMENT "同步化疗-频次（1:qw 2:q2w 3:q3w）",
  `tbhl_lc`  varchar(2)   NULL  COMMENT "同步化疗-疗程（0-10）",
  `sftbbx`  varchar(2)   NULL  COMMENT "同步靶向-是否（1:是  0:否）",
  `tbbx_ym`  varchar(100)   NULL  COMMENT "同步靶向-药名",
  `tbbx_jl`  varchar(4)   NULL  COMMENT "同步靶向-剂量（（100-200）mg/d1）",
  `tbbx_yf`  varchar(2)   NULL  COMMENT "同步靶向-用法（1:ivgtt 2:po）",
  `tbbx_pc`  varchar(2)   NULL  COMMENT "同步靶向-频次（1:qw 2:q2w 3:q3w）",
  `tbbx_cs`  varchar(2)   NULL  COMMENT "同步靶向-次数（0-8）",
  `sftbmy`  varchar(2)   NULL  COMMENT "同步免疫-是否（1:是  0:否）",
  `tbmy_ym`  varchar(100)   NULL  COMMENT "同步免疫-药名",
  `tbmy_jyl`  varchar(4)   NULL  COMMENT "同步免疫-剂量（（100-300）mg/d1）",
  `tbmy_yf`  varchar(2)   NULL  COMMENT "同步免疫-用法（1:ivgtt 2:po）",
  `tbmy_pc`  varchar(2)   NULL  COMMENT "同步免疫-频次（1:qw 2:q2w 3:q3w）",
  `tbmy_cs`  varchar(2)   NULL  COMMENT "同步免疫-次数（0-8）",
  `fljshlxpg_yfz`  varchar(2)   NULL  COMMENT "放疗结束疗效评估-原发灶（1:CR 2:PR 3:SD4:CD）",
  `fljshlxpg_jblbj`  varchar(2)   NULL  COMMENT "放疗结束疗效评估-颈部淋巴结（0:无 1:CR 2:PR3:SDCD）",
  `flbwbm`  varchar(20)   NULL  COMMENT "放疗部位编码",
  `flbwmc`  varchar(50)   NULL  COMMENT "放疗部位",
  `flbwcxbm`  varchar(20)   NULL  COMMENT "放疗部位侧性编码",
  `flbwcxmc`  varchar(50)   NULL  COMMENT "放疗部位侧性",
  `cyqk`  varchar(500)   NULL  COMMENT "放疗完成时情况",
  `cyzd_cydy`  varchar(500)   NULL  COMMENT "治疗后指导-出院带药",
  `cyzd_kfzd`  varchar(500)   NULL  COMMENT "治疗后指导-康复指导",
  `cyzd_sfjfz`  varchar(500)   NULL  COMMENT "治疗后指导-随访及复诊",
  `cyzd_xjsjzqk`  varchar(500)   NULL  COMMENT "治疗后指导-需及时就诊的情况",
  `zzys`  varchar(50)   NULL  COMMENT "主治医师",
  `zrfzrys`  varchar(50)   NULL  COMMENT "主任/副主任医生",
  `xjsj`  varchar(20)   NULL  COMMENT "小结时间",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_放疗小结';
-- 喉癌_首次病程录
DROP TABLE IF EXISTS coc_zy_hbzl_scbcl;
CREATE TABLE `coc_zy_hbzl_scbcl` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `kh`  varchar(32)   NOT NULL  COMMENT "卡号（患者就诊卡卡号）",
  `klx`  varchar(16)   NOT NULL  COMMENT "卡类型（参见字典表）",
  `xgbz`  varchar(1)   NOT NULL  COMMENT "修改标志（1:正常 2:修改3:撤销）",
  `yjlxh`  varchar(32)   NOT NULL  COMMENT "原纪录序号（院内唯一标识）",
  `mqqkjbstd`  varchar(2000)   NULL  COMMENT "目前情况及病史特点",
  `xbs`  varchar(2000)   NULL  COMMENT "现病史",
  `zyjws`  varchar(2000)   NULL  COMMENT "重要既往史",
  `tgjc`  varchar(2000)   NULL  COMMENT "体格检查",
  `zkjc`  varchar(2000)   NULL  COMMENT "专科检查",
  `fzjc`  varchar(2000)   NULL  COMMENT "辅助检查",
  `cbzd`  varchar(100)   NULL  COMMENT "初步诊断",
  `zdyj`  varchar(500)   NULL  COMMENT "诊断依据",
  `jbzd`  varchar(100)   NULL  COMMENT "鉴别诊断",
  `zljh`  varchar(2000)   NULL  COMMENT "诊疗计划",
  `zyys`  varchar(50)   NULL  COMMENT "住院医师",
  `zzys`  varchar(50)   NULL  COMMENT "主治医师",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_首次病程录';
-- 喉癌_病理报告-其他送检淋巴结
DROP TABLE IF EXISTS coc_zy_hbzl_blbg_qtsjlbj;
CREATE TABLE `coc_zy_hbzl_blbg_qtsjlbj` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `sjlbjqy`  varchar(10)   NULL  COMMENT "送检淋巴结区域",
  `sjlbjms`  varchar(10)   NULL  COMMENT "送检淋巴结枚数",
  `azyms`  varchar(10)   NULL  COMMENT "癌转移枚数",
  `yxlbjzdj`  varchar(10)   NULL  COMMENT "阳性淋巴结最大径（mm）",
  `ene`  varchar(2)   NULL  COMMENT "ENE（0:无 1:有）",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_病理报告-其他送检淋巴结';
-- 喉癌_入院记录（放疗）-体格检查
DROP TABLE IF EXISTS coc_zy_hbzl_ryjlfl_tgjc;
CREATE TABLE `coc_zy_hbzl_ryjlfl_tgjc` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `tw`  varchar(6)   NULL  COMMENT "体格检查-体温（℃）",
  `mb`  varchar(4)   NULL  COMMENT "体格检查-脉搏（次/分）",
  `hx`  varchar(4)   NULL  COMMENT "体格检查-呼吸（次/分）",
  `xy_shsy`  varchar(4)   NULL  COMMENT "体格检查-血压-收缩压（mmHg）",
  `xy_szy`  varchar(4)   NULL  COMMENT "体格检查-血压-舒张压（mmHg）",
  `KPS`  varchar(2)   NULL  COMMENT "体格检查-KPS评分",
  `sg`  varchar(6)   NULL  COMMENT "体格检查-身高（cm）",
  `tz`  varchar(6)   NULL  COMMENT "体格检查-体重（kg）",
  `tbmj`  varchar(6)   NULL  COMMENT "体格检查-体表面积（m2）",
  `fy`  varchar(2)   NULL  COMMENT "体格检查-发育（1:正常 2:不良）",
  `yy`  varchar(2)   NULL  COMMENT "体格检查-营养（1: 良好 2:中等3:不良 4:恶病质）",
  `mr`  varchar(2)   NULL  COMMENT "体格检查-面容（1:正常面容 2:慢性病容 3:贫血病容）",
  `bq`  varchar(2)   NULL  COMMENT "体格检查-表情（1: 自如 2:痛苦3:忧虑 4:淡漠）",
  `tiw`  varchar(2)   NULL  COMMENT "体格检查-体位（1: 自动体位 2:被动体位 3:强迫体位 4:强迫仰卧位5:强迫俯卧位 6:强迫侧卧位 7:强迫坐位 8:强迫蹲位 9:强迫停立位10:辗转体位 11:角弓反张位）",
  `shz`  varchar(2)   NULL  COMMENT "体格检查-神志（1:清楚 2:淡漠3:嗜睡 4:昏睡5:谵妄 6:浅昏迷7:深昏迷）",
  `jszt`  varchar(2)   NULL  COMMENT "体格检查-精神状态（1: 良好 2:一般3:较差 4:很差）",
  `cthz`  varchar(2)   NULL  COMMENT "体格检查-查体（1:合作 0:不合作）",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_入院记录（放疗）-体格检查';
-- 喉癌_门诊病史
DROP TABLE IF EXISTS coc_zy_hbzl_mzbs;
CREATE TABLE `coc_zy_hbzl_mzbs` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `kh`  varchar(32)   NOT NULL  COMMENT "卡号（患者就诊卡卡号）",
  `klx`  varchar(16)   NOT NULL  COMMENT "卡类型（参见字典表）",
  `xgbz`  varchar(1)   NOT NULL  COMMENT "修改标志（1:正常 2:修改3:撤销）",
  `yjlxh`  varchar(32)   NOT NULL  COMMENT "原纪录序号（院内唯一标识）",
  `hzxm`  varchar(50)   NULL  COMMENT "姓名",
  `hzxb`  varchar(10)   NULL  COMMENT "性别",
  `hznl`  varchar(10)   NULL  COMMENT "年龄",
  `hzjg`  varchar(100)   NULL  COMMENT "籍贯",
  `hzmz`  varchar(20)   NULL  COMMENT "民族",
  `hzcsd`  varchar(100)   NULL  COMMENT "出生地",
  `hzhy`  varchar(20)   NULL  COMMENT "婚姻",
  `hzzy`  varchar(50)   NULL  COMMENT "职业",
  `bscsz`  varchar(50)   NULL  COMMENT "病史陈述者",
  `jlrq`  varchar(20)   NULL  COMMENT "记录日期",
  `zs`  varchar(2000)   NULL  COMMENT "主诉",
  `bsms_fbsj`  varchar(20)   NULL  COMMENT "病史描述-发病时间",
  `bsms_fbzz`  varchar(200)   NULL  COMMENT "病史描述-发病症状",
  `bsms_yhtt`  varchar(2)   NULL  COMMENT "病史描述-咽喉疼痛（1:伴  0:不伴）",
  `bsms_hxkn`  varchar(2)   NULL  COMMENT "病史描述-呼吸困难（1:伴  0:不伴）",
  `bsms_jbbk`  varchar(2)   NULL  COMMENT "病史描述-颈部包块（1:伴  0:不伴）",
  `bsms_tzdx`  varchar(2)   NULL  COMMENT "病史描述-痰中带血（1:伴  0:不伴）",
  `bsms_sysytz`  varchar(200)   NULL  COMMENT "病史描述-声音嘶哑特征",
  `bsms_ks`  varchar(2)   NULL  COMMENT "病史描述-咳嗽（1:有  0:无）",
  `bsms_tykn`  varchar(2)   NULL  COMMENT "病史描述-吞咽困难（1:有  0:无）",
  `bsms_hj`  varchar(2)   NULL  COMMENT "病史描述-活检（1:有  0:无）",
  `bsms_hj_jcsj`  varchar(20)   NULL  COMMENT "病史描述-喉镜-检查时间",
  `bsms_hj_jcdw`  varchar(2)   NULL  COMMENT "病史描述-喉镜-检查医院（1:我院 2:外院）",
  `bsms_hj_jcjg`  varchar(500)   NULL  COMMENT "病史描述-喉镜-检查结果",
  `bsms_jbCT_jcsj`  varchar(20)   NULL  COMMENT "病史描述-颈部CT-检查时间",
  `bsms_jbCT_jcdw`  varchar(2)   NULL  COMMENT "病史描述-颈部CT-检查医院（1:我院 2:外院）",
  `bsms_jbCT_jcjg`  varchar(500)   NULL  COMMENT "病史描述-颈部CT-检查结果",
  `jws_ywgms`  varchar(2)   NULL  COMMENT "既往史-药物过敏史（1:有  0:无）",
  `tgjc_yb`  varchar(2)   NULL  COMMENT "体格检查-咽部（1:正常 0:不正常）",
  `tgjc_jjhjxjhy`  varchar(2)   NULL  COMMENT "体格检查-间接喉镜下见会厌（1:正常 0:不正常）",
  `tgjc_zcshd`  varchar(2)   NULL  COMMENT "体格检查-左侧声带（1:正常 0:不正常）",
  `tgjc_ycshd`  varchar(2)   NULL  COMMENT "体格检查-右侧声带（1:正常 0:不正常）",
  `tgjc_zcsd`  varchar(2)   NULL  COMMENT "体格检查-左侧室带（1:正常 0:不正常）",
  `tgjc_ycsd`  varchar(2)   NULL  COMMENT "体格检查-右侧室带（1:正常 0:不正常）",
  `tgjc_jbzdlbj`  varchar(2)   NULL  COMMENT "体格检查-颈部肿大淋巴结（1:扪及 0:未扪及）",
  `cbzd`  varchar(100)   NULL  COMMENT "初步诊断",
  `cl`  varchar(2000)   NULL  COMMENT "处理",
  `sxz`  varchar(50)   NULL  COMMENT "书写者",
  `cjsj`  varchar(20)   NULL  COMMENT "创建时间",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_门诊病史';
-- 喉癌_住院MDT记录
DROP TABLE IF EXISTS coc_zy_hbzl_zymdtjl;
CREATE TABLE `coc_zy_hbzl_zymdtjl` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `kh`  varchar(32)   NOT NULL  COMMENT "卡号（患者就诊卡卡号）",
  `klx`  varchar(16)   NOT NULL  COMMENT "卡类型（参见字典表）",
  `xgbz`  varchar(1)   NOT NULL  COMMENT "修改标志（1:正常 2:修改3:撤销）",
  `yjlxh`  varchar(32)   NOT NULL  COMMENT "原纪录序号（院内唯一标识）",
  `hzxm`  varchar(50)   NULL  COMMENT "患者姓名",
  `bq`  varchar(50)   NULL  COMMENT "病区",
  `ch`  varchar(20)   NULL  COMMENT "床号",
  `ks`  varchar(50)   NULL  COMMENT "科室",
  `zyh`  varchar(20)   NULL  COMMENT "住院号",
  `tlsj`  varchar(20)   NULL  COMMENT "讨论时间",
  `fqks`  varchar(50)   NULL  COMMENT "发起科室",
  `fqrxm`  varchar(50)   NULL  COMMENT "发起人姓名",
  `fqkscyry  zrys`  varchar(50)   NULL  COMMENT "发起科室参与人员-主任医师",
  `fqkscyry  zzys`  varchar(50)   NULL  COMMENT "发起科室参与人员-主治医师",
  `fqkscyry  zyys`  varchar(50)   NULL  COMMENT "发起科室参与人员-住院医师",
  `zzyshbbs`  varchar(2000)   NULL  COMMENT "主治医师汇报病史",
  `zrxm`  varchar(50)   NULL  COMMENT "主任姓名",
  `zryj`  varchar(500)   NULL  COMMENT "主任意见",
  `cyks`  varchar(50)   NULL  COMMENT "参与科室",
  `cyry`  varchar(100)   NULL  COMMENT "参与人员",
  `cyksysyj`  varchar(500)   NULL  COMMENT "参与科室医师意见",
  `tljg`  varchar(500)   NULL  COMMENT "讨论结果",
  `czyj`  varchar(500)   NULL  COMMENT "处置意见",
  `yqxgfx`  varchar(500)   NULL  COMMENT "预期效果风险",
  `zysx`  varchar(500)   NULL  COMMENT "注意事项",
  `jlysqm`  varchar(50)   NULL  COMMENT "记录医师签名",
  `jlysqmrq`  varchar(20)   NULL  COMMENT "记录医师签名日期",
  `sjysqm`  varchar(50)   NULL  COMMENT "上级医师签名",
  `sjysqmrq`  varchar(20)   NULL  COMMENT "上级医师签名日期",
  `zrysqm`  varchar(50)   NULL  COMMENT "主任医师签名",
  `zrysqmrq`  varchar(20)   NULL  COMMENT "主任医师签名日期",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_住院MDT记录';
-- 喉癌_电子喉镜报告
DROP TABLE IF EXISTS coc_zy_hbzl_hjbg;
CREATE TABLE `coc_zy_hbzl_hjbg` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `kh`  varchar(32)   NOT NULL  COMMENT "卡号（患者就诊卡卡号）",
  `klx`  varchar(16)   NOT NULL  COMMENT "卡类型（参见字典表）",
  `xgbz`  varchar(1)   NOT NULL  COMMENT "修改标志（1:正常 2:修改3:撤销）",
  `yjlxh`  varchar(32)   NOT NULL  COMMENT "原纪录序号（院内唯一标识）",
  `hzxm`  varchar(50)   NULL  COMMENT "姓名",
  `hzxb`  varchar(10)   NULL  COMMENT "性别",
  `hznl`  varchar(10)   NULL  COMMENT "年龄",
  `hzzyhmzh`  varchar(20)   NULL  COMMENT "住院号/门诊号",
  `jcrq`  varchar(20)   NULL  COMMENT "检查日期",
  `jcsj_zbtt`  varchar(2)   NULL  COMMENT "左扁桃体（1:光滑 2:溃疡 3:充血 4:分泌物 5:新生物 6:I度 7:II度 8:III度 9:异物 10:其他）",
  `jcsj_zbtt_qtms`  varchar(200)   NULL  COMMENT "左扁桃体-其他描述",
  `jcsj_ybtt`  varchar(2)   NULL  COMMENT "右扁桃体（1:光滑 2:溃疡 3:充血 4:分泌物 5:新生物 6:I度 7:II度 8:III度 9:异物 10:其他）",
  `jcsj_ybtt_qtms`  varchar(200)   NULL  COMMENT "右扁桃体-其他描述",
  `jcsj_kyhb`  varchar(2)   NULL  COMMENT "口咽后壁（1:光滑 2:粗糙 3:溃疡 4:充血 5:肿胀 6:囊肿样物 7:淋巴样组织 8:新生物 9:其他）",
  `jcsj_kyhb_qms`  varchar(200)   NULL  COMMENT "口咽后壁-其他描述",
  `jcsj_ycb`  varchar(2)   NULL  COMMENT "咽侧壁（1:光滑 2:粗糙 3:溃疡 4:内移 5:新生物 6:其他）",
  `jcsj_ycb_qtms`  varchar(200)   NULL  COMMENT "咽侧壁-其他描述",
  `jcsj_sg`  varchar(2)   NULL  COMMENT "舌根（1:光滑 2:粗糙 3:溃疡 4:囊肿样物 5:淋巴样组织 6:新生物 7:异物 8:其他）",
  `jcsj_sg_qtms`  varchar(200)   NULL  COMMENT "舌根-其他描述",
  `jcsj_hysm`  varchar(2)   NULL  COMMENT "会厌舌面（1:光滑 2:粗糙 3:溃疡 4:充血 5:肿胀 6:囊肿样物 7:淋巴样组织 8:新生物 9:未暴露 10:其他）",
  `jcsj_hysm_qtms`  varchar(200)   NULL  COMMENT "会厌舌面-其他描述",
  `jcsj_hyhm`  varchar(2)   NULL  COMMENT "会厌喉面（1:光滑 2:粗糙 3:溃疡 4:新生物 5:其他）",
  `jcsj_hyhm_qtms`  varchar(200)   NULL  COMMENT "会厌喉面-其他描述",
  `jcsj_zshid`  varchar(2)   NULL  COMMENT "左室带（1:光滑 2:粗糙 3:溃疡 4:充血 5:肥厚 6:新生物 7:其他）",
  `jcsj_zshid_qtms`  varchar(200)   NULL  COMMENT "左室带-其他描述",
  `jcsj_yshd`  varchar(2)   NULL  COMMENT "右室带（1:光滑 2:粗糙 3:溃疡 4:充血 5:肥厚 6:新生物 7:其他）",
  `jcsj_yshd_qtms`  varchar(200)   NULL  COMMENT "右室带-其他描述",
  `jcsj_zpl`  varchar(2)   NULL  COMMENT "左披裂（1:光滑 2:粗糙 3:溃疡 4:充血 5:肿胀 6:囊肿样物 7:淋巴样组织 8:新生物 9:其他）",
  `jcsj_zpl_qtms`  varchar(200)   NULL  COMMENT "左披裂-其他描述",
  `jcsj_ypl`  varchar(2)   NULL  COMMENT "右披裂（1:光滑 2:粗糙 3:溃疡 4:充血 5:肿胀 6:囊肿样物 7:淋巴样组织 8:新生物 9:其他）",
  `jcsj_ypl_qtms`  varchar(200)   NULL  COMMENT "右披裂-其他描述",
  `jcsj_zsd`  varchar(2)   NULL  COMMENT "左声带（1:光滑 2:粗糙 3:急性充血4:慢性充血 5:出血 6:肿胀7:肥厚 8:小结 9:息肉样物10:囊肿样物 11:白斑样物12:肉芽样物 13:其他新生物）",
  `jcsj_zsd_qtxswms`  varchar(200)   NULL  COMMENT "左声带-其他新生物描述",
  `jcsj_zsdyd`  varchar(2)   NULL  COMMENT "左声带运动（1:活动好 2:活动受限 3:固定）",
  `jcsj_ysd`  varchar(2)   NULL  COMMENT "右声带（1:光滑 2:粗糙 3:急性充血4:慢性充血 5:出血 6:肿胀7:肥厚 8:小结 9:息肉样物10:囊肿样物 11:白斑样物12:肉芽样物 13:其他新生物）",
  `jcsj_ysd_qtxswms`  varchar(200)   NULL  COMMENT "右声带-其他新生物描述",
  `jcsj_ysdyd`  varchar(2)   NULL  COMMENT "右声带运动（1:活动好 2:活动受限 3:固定）",
  `jcsj_zlzw`  varchar(2)   NULL  COMMENT "左梨状窝（1:光滑 2:异物 3:新生物 4:积液 5:淋巴样组织 6:其他）",
  `jcsj_zlzw_qtms`  varchar(200)   NULL  COMMENT "左梨状窝-其他描述",
  `jcsj_ylzw`  varchar(2)   NULL  COMMENT "右梨状窝（1:光滑 2:异物 3:新生物 4:积液 5:淋巴样组织 6:其他）",
  `jcsj_ylzw_qtms`  varchar(200)   NULL  COMMENT "右梨状窝-其他描述",
  `jcsj_xyhb`  varchar(2)   NULL  COMMENT "下咽后壁（1:光滑 2:异物 3:新生物 4:淋巴样组织 5:出血 6:肿胀7:其他）",
  `jcsj_xyhb_qtms`  varchar(200)   NULL  COMMENT "下咽后壁-其他描述",
  `jcsj_hhq`  varchar(2)   NULL  COMMENT "环后区（1:光滑 2:异物 3:新生物 4:淋巴样组织 5:出血 6:肿胀7:其他）",
  `jcsj_hhq_qtms`  varchar(200)   NULL  COMMENT "环后区-其他描述",
  `jcsj_smx`  varchar(2)   NULL  COMMENT "声门下（1:光滑 2:异物 3:新生物 4:出血 5:肿胀 6:其他）",
  `jcsj_smx_qtms`  varchar(200)   NULL  COMMENT "声门下-其他描述",
  `jcsj_nbizdcxfj`  varchar(20)   NULL  COMMENT "NBI窄带成像分级",
  `jcsj_qt`  varchar(500)   NULL  COMMENT "其他",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_电子喉镜报告';
-- 喉癌_入院记录（放疗）-专科检查
DROP TABLE IF EXISTS coc_zy_hbzl_ryjlfl_zkjc;
CREATE TABLE `coc_zy_hbzl_ryjlfl_zkjc` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `ywbsg`  varchar(2)   NULL  COMMENT "专科检查-有无鼻饲管（1:有 0:无）",
  `bsgbw`  varchar(2)   NULL  COMMENT "专科检查-鼻饲管部位（1:左鼻 2:右鼻）",
  `zkmcj`  varchar(4)   NULL  COMMENT "专科检查-张口门齿距（cm）",
  `yeqk`  varchar(2)   NULL  COMMENT "专科检查-硬腭（1:光滑 2:隆起3:溃疡 4:缺损）",
  `reqk`  varchar(2)   NULL  COMMENT "专科检查-软腭（1:光滑 2:溃疡3:上抬受限）",
  `bttzdcd`  varchar(2)   NULL  COMMENT "专科检查-扁桃体肿大程度（0:无肿大 1: Ⅰ度肿大 2: Ⅱ度肿大3:Ⅲ度肿大）",
  `bttzdcb`  varchar(2)   NULL  COMMENT "专科检查-扁桃体肿大侧别（1:双侧 2:左侧3:右侧）",
  `htywzd`  varchar(2)   NULL  COMMENT "专科检查-喉体有无增大（1:有 0:无）",
  `jbywqgtg`  varchar(2)   NULL  COMMENT "专科检查-颈部有无气管套管（1:有 0:无）",
  `qgtglx`  varchar(2)   NULL  COMMENT "专科检查-气管套管类型（1:金属 2:硅塑）",
  `ywqgtgdk`  varchar(2)   NULL  COMMENT "专科检查-气管套管堵管-有无（1:有 0:无）",
  `ywqhqgt`  varchar(2)   NULL  COMMENT "专科检查-全喉气管筒-有无（1:有 0:无）",
  `qhqgtlx`  varchar(2)   NULL  COMMENT "专科检查-全喉气管筒类型（12mm/14mm）",
  `qhqgtzk`  varchar(2)   NULL  COMMENT "专科检查-全喉气管筒造口（1:光滑 0:不光滑）",
  `hynm`  varchar(2)   NULL  COMMENT "专科检查-喉咽黏膜（1:光滑 2:溃疡3:局部隆起）",
  `lzwnmqk`  varchar(2)   NULL  COMMENT "专科检查-梨状窝黏膜（1:光滑 2:溃疡3:局部隆起）",
  `lzwnmyccb`  varchar(2)   NULL  COMMENT "专科检查-梨状窝黏膜异常侧别（1:双侧 2:左侧3:右侧）",
  `hyqk`  varchar(2)   NULL  COMMENT "专科检查-会厌（1:光滑 2:红肿3:溃疡）",
  `plqk`  varchar(2)   NULL  COMMENT "专科检查-披裂（1:光滑 2:溃疡3:局部隆起）",
  `plyccb`  varchar(2)   NULL  COMMENT "专科检查-披裂异常侧别（1:双侧 2:左侧3:右侧）",
  `sdqk`  varchar(2)   NULL  COMMENT "专科检查-声带（1:光滑 2:水肿）",
  `sdyccb`  varchar(2)   NULL  COMMENT "专科检查-声带异常侧别（1:双侧 2:左侧3:右侧）",
  `sdhdqk`  varchar(2)   NULL  COMMENT "专科检查-声带活动（1:正常 2:受限3:麻痹）",
  `sdhdyccb`  varchar(2)   NULL  COMMENT "专科检查-声带活动异常侧别（1:双侧 2:左侧3:右侧）",
  `sml`  varchar(2)   NULL  COMMENT "专科检查-声门裂（1:正常 2:狭窄）",
  `ty`  varchar(2)   NULL  COMMENT "专科检查-吞咽（1:正常 2:呛咳）",
  `shs`  varchar(2)   NULL  COMMENT "专科检查-伸舌（1:居中 2:左偏3:右偏）",
  `mbgj`  varchar(2)   NULL  COMMENT "专科检查-面部感觉（1:正常 2:麻木）",
  `mbgjyccb`  varchar(2)   NULL  COMMENT "专科检查-面部感觉异常侧别（1:双侧 2:左侧3:右侧）",
  `jbpfqk`  varchar(2)   NULL  COMMENT "专科检查-颈部皮2肤情况（1:正常 2:溃疡）",
  `jbpfyccb`  varchar(2)   NULL  COMMENT "专科检查-颈部皮肤异常侧别（1:双侧 2:左侧3:右侧）",
  `ywlbjzd`  varchar(2)   NULL  COMMENT "专科检查-淋巴结肿大-有无（1:有 0:无）",
  `lbjzdcb`  varchar(2)   NULL  COMMENT "专科检查-淋巴结肿大侧别（1:双侧 2:左侧3:右侧）",
  `lbjzdbw`  varchar(2)   NULL  COMMENT "专科检查-淋巴结肿大部位（1:上颈部淋巴结2:中颈部淋巴结3:下颈部淋巴结）",
  `lbjzdzj`  varchar(2)   NULL  COMMENT "专科检查-淋巴结肿大直径（cm）",
  `lbjzdzd`  varchar(2)   NULL  COMMENT "专科检查-淋巴结肿大质地（1:韧 2:硬）",
  `lbjzdhdqk`  varchar(2)   NULL  COMMENT "专科检查-淋巴结肿大活动情况（1:活动受限 2:固定）",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_入院记录（放疗）-专科检查';
-- 喉癌_入院记录（放疗）-既往史
DROP TABLE IF EXISTS coc_zy_hbzl_ryjlfl_jws;
CREATE TABLE `coc_zy_hbzl_ryjlfl_jws` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `crbs`  varchar(2)   NULL  COMMENT "既往史-传染病史（0:无 1有）",
  `crbs_sc`  varchar(10)   NULL  COMMENT "既往史-传染病史-时长（年/月）",
  `crbs_zlfs`  varchar(200)   NULL  COMMENT "既往史-传染病史-治疗方式",
  `crbs_mqqk`  varchar(2)   NULL  COMMENT "既往史-传染病史-目前情况（0:不稳定 1:稳定）",
  `sswss`  varchar(2)   NULL  COMMENT "既往史-手术外伤史（0:无 1有）",
  `sswss_sswssj`  varchar(10)   NULL  COMMENT "既往史-手术外伤史-手术外伤时间",
  `sswss_sswsyy`  varchar(200)   NULL  COMMENT "既往史-手术外伤史-手术外伤原因",
  `sswss_sswsms`  varchar(200)   NULL  COMMENT "既往史-手术外伤史-手术外伤描述",
  `sxs`  varchar(2)   NULL  COMMENT "既往史-输血史（0:无 1有）",
  `sxs_sxsj`  varchar(10)   NULL  COMMENT "既往史-输血史-输血时间",
  `sxs_sxyy`  varchar(100)   NULL  COMMENT "既往史-输血史-输血原因",
  `sxs_sxxx`  varchar(2)   NULL  COMMENT "既往史-输血史-输血血型（1:A型 2:型 3:O型 4:AB型）",
  `sxs_sxl`  varchar(2)   NULL  COMMENT "既往史-输血史-输血量（ml）",
  `sxs_sxfy`  varchar(2)   NULL  COMMENT "既往史-输血史-输血反应（0:无 1有）",
  `sxs_sxfybx`  varchar(2)   NULL  COMMENT "既往史-输血史-输血反应表现",
  `gms`  varchar(2)   NULL  COMMENT "既往史-过敏史（0:无 1有）",
  `gms_gmy_gmy`  varchar(200)   NULL  COMMENT "既往史-过敏史-过敏源",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_入院记录（放疗）-既往史';
-- 喉癌_入院记录
DROP TABLE IF EXISTS coc_zy_hbzl_ryjl;
CREATE TABLE `coc_zy_hbzl_ryjl` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `kh`  varchar(32)   NOT NULL  COMMENT "卡号（患者就诊卡卡号）",
  `klx`  varchar(16)   NOT NULL  COMMENT "卡类型（参见字典表）",
  `xgbz`  varchar(1)   NOT NULL  COMMENT "修改标志（1:正常 2:修改3:撤销）",
  `yjlxh`  varchar(32)   NOT NULL  COMMENT "原纪录序号（院内唯一标识）",
  `hzxm`  varchar(50)   NULL  COMMENT "姓名",
  `hzxb`  varchar(10)   NULL  COMMENT "性别",
  `hznl`  varchar(10)   NULL  COMMENT "年龄",
  `hzmz`  varchar(20)   NULL  COMMENT "民族",
  `hzhy`  varchar(20)   NULL  COMMENT "婚姻",
  `hzjg`  varchar(50)   NULL  COMMENT "籍贯",
  `hzzy`  varchar(20)   NULL  COMMENT "职业",
  `rysj`  varchar(20)   NULL  COMMENT "入院时间",
  `jtdz`  varchar(100)   NULL  COMMENT "家庭地址",
  `bscjrq`  varchar(20)   NULL  COMMENT "病史采集日期",
  `bscsz`  varchar(2)   NULL  COMMENT "病史陈述者（1:患者本人 2:患者家属 3:其他）",
  `gzdw`  varchar(100)   NULL  COMMENT "工作单位",
  `kkcd`  varchar(2)   NULL  COMMENT "可靠程度（0:不可靠 1:可靠）",
  `zs`  varchar(2000)   NULL  COMMENT "主诉",
  `hys`  varchar(2)   NULL  COMMENT "婚育史（1:未婚未育 2:已婚已育，家人体健 3:已婚未育）",
  `jzycbs`  varchar(2)   NULL  COMMENT "家族遗传病史（1:有 0:无）",
  `jzycbs_qsgx`  varchar(2)   NULL  COMMENT "家族遗传病史-亲属关系（1:父亲 2:母亲3:兄弟 4:姐妹5:儿子 6:女儿）",
  `jzycbs_jbmc`  varchar(100)   NULL  COMMENT "家族遗传病史-疾病名称",
  `cbzd_mc`  varchar(100)   NULL  COMMENT "初步诊断-名称",
  `cbzd_t`  varchar(2)   NULL  COMMENT "初步诊断-T（1:X 2:0 3:14:2 5:3 6:4）",
  `cbzd_n`  varchar(2)   NULL  COMMENT "初步诊断-N（1:X 2:0 3:14:2 5:3）",
  `cbzd_m`  varchar(2)   NULL  COMMENT "初步诊断-M（1:0 2:1）",
  `cbzd_fq`  varchar(2)   NULL  COMMENT "初步诊断-分期（1:0 2:I 3:II4:III 5:IVA6:IVB 7:IVC）",
  `zyys_qm`  varchar(50)   NULL  COMMENT "住院医师签名",
  `zyys_qmsj`  varchar(20)   NULL  COMMENT "住院医师签名时间",
  `zzys_qm`  varchar(50)   NULL  COMMENT "主治医师签名",
  `zzys_qmsj`  varchar(20)   NULL  COMMENT "主治医师签名时间",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_入院记录';
-- 喉癌_入院记录（放疗）-现病史
DROP TABLE IF EXISTS coc_zy_hbzl_ryjlfl_xbs; 
CREATE TABLE `coc_zy_hbzl_ryjlfl_xbs` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `fbrq`  varchar(20)   NULL  COMMENT "现病史-发病日期",
  `fbcb`  varchar(2)   NULL  COMMENT "现病史-发病侧别（1:左 2:右 3:双侧）",
  `fbzz`  varchar(2)   NULL  COMMENT "现病史-发病症状（1:颈部肿块 2:声嘶 3:咽部不适感4:咽喉疼痛 5:咽部异物感 6:咳嗽伴有 7:无痰中带血 8:呼吸困难9:其他）",
  `dzhj`  varchar(2)   NULL  COMMENT "现病史-电子喉镜（1:有  0:无）",
  `hbCT`  varchar(2)   NULL  COMMENT "现病史-喉部CT（1:有  0:无）",
  `hbMRI`  varchar(2)   NULL  COMMENT "现病史-喉部MRI（1:有  0:无）",
  `jbcsjc`  varchar(2)   NULL  COMMENT "现病史-颈部超声检查（1:有  0:无）",
  `jcfx`  varchar(2)   NULL  COMMENT "现病史-检查发现（1:会厌舌面新生物 2:会厌喉面新生物 3:咽会厌襞新生物 4:杓会厌襞新生物 5:声带新生物 6:室带新生物 7:喉室新生物 8:披裂新生物9:声门下新生物10:左颈部淋巴结肿大 11:右颈部淋巴结肿大）",
  `jlbjcc`  varchar(2)   NULL  COMMENT "现病史-颈淋巴结穿刺（1:有  0:无）",
  `hbxswhj`  varchar(2)   NULL  COMMENT "现病史-喉部新生物活检（1:有  0:无）",
  `blbw`  varchar(2)   NULL  COMMENT "现病史-病理部位（1:颈部 2:会厌舌面 3:会厌喉面4:咽会厌襞 5:杓会厌襞 6:声带7:室带 8:喉室9:披裂 10:声门下）",
  `blzd`  varchar(2)   NULL  COMMENT "现病史-病理诊断（1:鳞状细胞癌 2:鳞癌Ⅱ级 3:小区癌变 4:高级别上皮内瘤变 5:其他）",
  `ywwyss`  varchar(2)   NULL  COMMENT "现病史-有无外院手术（1:有  0:无）",
  `wysssj`  varchar(20)   NULL  COMMENT "现病史-外院手术日期",
  `wyssmc`  varchar(100)   NULL  COMMENT "现病史-外院手术名称",
  `ywhl`  varchar(2)   NULL  COMMENT "现病史-有无化疗（1:有  0:无）",
  `hlyyjlc`  varchar(200)   NULL  COMMENT "现病史-化疗具体用药及疗程",
  `ryyy`  varchar(200)   NULL  COMMENT "现病史-入院原因",
  `hzsz`  varchar(2)   NULL  COMMENT "现病史-患者神智（1:清晰 2:淡漠3:模糊 4:昏睡5:谵妄 6:昏迷）",
  `jszt`  varchar(2)   NULL  COMMENT "现病史-精神状态（1: 良好 2:一般3:较差 4:很差）",
  `tlqk`  varchar(2)   NULL  COMMENT "现病史-体力情况（1: 良好 2:一般3:较差 4:很差）",
  `sysl`  varchar(2)   NULL  COMMENT "现病史-食欲食量（1: 良好 2:一般3:较差 4:很差）",
  `smqk`  varchar(2)   NULL  COMMENT "现病史-睡眠情况（1: 良好 2:一般3:较差 4:很差）",
  `tzbh`  varchar(2)   NULL  COMMENT "现病史-体重变化（0:无明显变化 1:体重明显增加 2:体重减轻）",
  `tzbhsz`  varchar(6)   NULL  COMMENT "现病史-体重变化数值（Kg）",
  `dbqk`  varchar(2)   NULL  COMMENT "现病史-大便（1:正常 2:腹泻3:便秘 4;其他）",
  `xbqk`  varchar(2)   NULL  COMMENT "现病史-小便（1:正常 2:血尿3:尿频 4:其他）",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_入院记录（放疗）-现病史';
-- 喉癌_病理报告
DROP TABLE IF EXISTS coc_zy_hbzl_blbg;
CREATE TABLE `coc_zy_hbzl_blbg` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `kh`  varchar(32)   NOT NULL  COMMENT "卡号（患者就诊卡卡号）",
  `klx`  varchar(16)   NOT NULL  COMMENT "卡类型（参见字典表）",
  `xgbz`  varchar(1)   NOT NULL  COMMENT "修改标志（1:正常 2:修改3:撤销）",
  `yjlxh`  varchar(32)   NOT NULL  COMMENT "原纪录序号（院内唯一标识）",
  `hzxm`  varchar(50)   NULL  COMMENT "姓名",
  `sfzh`  varchar(20)   NULL  COMMENT "身份证号",
  `blh`  varchar(20)   NULL  COMMENT "病理号",
  `hzbq`  varchar(50)   NULL  COMMENT "病区",
  `hzch`  varchar(20)   NULL  COMMENT "床号",
  `hzxb`  varchar(10)   NULL  COMMENT "性别",
  `hznl`  varchar(10)   NULL  COMMENT "年龄",
  `zyh`  varchar(20)   NULL  COMMENT "住院号",
  `sdrq`  varchar(20)   NULL  COMMENT "收到日期",
  `bblx`  varchar(2)   NULL  COMMENT "标本类型（1:全喉 2:部分喉 3:部分咽4:全下咽 5:食管 6:舌根7:其他）",
  `zlwz`  varchar(2)   NULL  COMMENT "肿瘤位置（1:左声带 2:右声带 3:左室带 4:右室带 5:左喉室 6:右喉室 7:左喉前庭 8:右喉前庭 9:前联合 10:后中线 11:会厌喉面 12:会厌舌面 13:会厌上部 14:会厌中部 15:会厌下部 20:左披裂 17:左披会皱襞 18:右披裂 19:右披会皱襞 20:左侧梨状窝21:右侧梨状窝 22:左喉咽侧壁 23:右喉咽侧壁 24:咽后壁 25:食道入口 26:舌根27:左口咽侧壁 28:右口咽侧壁 29:环后区 30:不清）",
  `zlzsm`  varchar(2)   NULL  COMMENT "肿瘤灶数目（单灶填1，多灶填写具体数目）",
  `zldx_zx`  varchar(20)   NULL  COMMENT "肿瘤大小-最小（单灶的大小；多灶的最小格式：× × mm）",
  `zldx_zd`  varchar(20)   NULL  COMMENT "肿瘤大小-最大（多灶的最大格式：××mm）",
  `zldxbnclyy`  varchar(200)   NULL  COMMENT "肿瘤大小不能测量原因",
  `zzxlx`  varchar(2)   NULL  COMMENT "组织学类型（1:鳞状细胞癌 ICD-O编码8070/3     2:鳞状细胞癌亚型:疣状癌 ICD-O编码8051/33:鳞状细胞癌亚型:基底样鳞状细胞癌 ICD-O编码8083/34:鳞状细胞癌亚型:乳头状鳞状细胞癌 ICD-O编码8052/35:鳞状细胞癌亚型:梭形细胞鳞状细胞癌 ICD-O编码8074/3    6:鳞状细胞癌亚型:腺鳞癌 ICD-O编码8560/37:淋巴上皮癌 ICD-O编码8082/3   8:其他）",
  `zzxfh`  varchar(2)   NULL  COMMENT "组织学分化（1:高分化 2:中分化 3:低分化 4:其他）",
  `jrzzsd`  varchar(200)   NULL  COMMENT "浸润组织深度",
  `sjqf`  varchar(2)   NULL  COMMENT "神经侵犯（0:无 1:有 2:不确定）",
  `mgqf`  varchar(2)   NULL  COMMENT "脉管侵犯（0:无 1:有 2:不确定）",
  `qysjqk`  varchar(2)   NULL  COMMENT "切缘送检情况（1:送检 0:未送检）",
  `jqyzj`  varchar(4)   NULL  COMMENT "距切缘最近（mm）",
  `sqylj`  varchar(2)   NULL  COMMENT "上切缘累及（0:未累及 1:累及：浸润癌2: 累及：原位癌 3: 累及：高级别异型增生）",
  `xqylj`  varchar(2)   NULL  COMMENT "下切缘累及（0:未累及 1:累及：浸润癌2: 累及：原位癌 3: 累及：高级别异型增生）",
  `zqylj`  varchar(2)   NULL  COMMENT "左切缘累及（0:未累及 1:累及：浸润癌2: 累及：原位癌 3: 累及：高级别异型增生）",
  `yqylj`  varchar(2)   NULL  COMMENT "右切缘累及（0:未累及 1:累及：浸润癌2: 累及：原位癌 3: 累及：高级别异型增生）",
  `jdqy`  varchar(2)   NULL  COMMENT "基底切缘（0:未暴露 1:暴露 2:可疑暴露）",
  `bmqy`  varchar(2)   NULL  COMMENT "表面切缘（0:未暴露 1:暴露 2:可疑暴露）",
  `lbj_gzxzjb_sjlbjms`  varchar(10)   NULL  COMMENT "淋巴结-根治性左颈部-送检淋巴结枚数",
  `lbj_gzxzjb  azyms`  varchar(10)   NULL  COMMENT "淋巴结-根治性左颈部-癌转移枚数",
  `lbj_gzxzjb_zylbjwyxsrtjbw`  varchar(2)   NULL  COMMENT "淋巴结-根治性左颈部-转移淋巴结位于胸锁乳突肌部位（1:上段 2:中段 3:下段）",
  `lbj_gzxzjb_lbjzdj`  varchar(10)   NULL  COMMENT "淋巴结-根治性左颈部-淋巴结最大径（mm）",
  `lbj_gzxzjb   ene`  varchar(2)   NULL  COMMENT "淋巴结-根治性左颈部-ENE（0:无 1:有）",
  `lbj_gzxyjb_sjlbjms`  varchar(10)   NULL  COMMENT "淋巴结-根治性右颈部-送检淋巴结枚数",
  `lbj_gzxyjb  azyms`  varchar(10)   NULL  COMMENT "淋巴结-根治性右颈部-癌转移枚数",
  `lbj_gzxyjb_zylbjwyxsrtjbw`  varchar(2)   NULL  COMMENT "淋巴结-根治性右颈部-转移淋巴结位于胸锁乳突肌部位（1:上段 2:中段 3:下段）",
  `lbj_gzxyjb_lbjzdj`  varchar(10)   NULL  COMMENT "淋巴结-根治性右颈部-淋巴结最大径（mm）",
  `lbj_gzxyjb   ene`  varchar(2)   NULL  COMMENT "淋巴结-根治性右颈部-ENE（0:无 1:有）",
  `lbj_gnxzjb_sjlbjms`  varchar(10)   NULL  COMMENT "淋巴结-功能性左颈部-送检淋巴结枚数",
  `lbj_gnxzjb  azyms`  varchar(10)   NULL  COMMENT "淋巴结-功能性左颈部-癌转移枚数",
  `lbj_gnxzjb_lbjzdj`  varchar(10)   NULL  COMMENT "淋巴结-功能性左颈部-淋巴结最大径（mm）",
  `lbj_gnxzjb   ene`  varchar(2)   NULL  COMMENT "淋巴结-功能性左颈部-ENE（0:无 1:有）",
  `lbj_gnxyjb_sjlbjms`  varchar(10)   NULL  COMMENT "淋巴结-功能性右颈部-送检淋巴结枚数",
  `lbj_gnxyjb  azyms`  varchar(10)   NULL  COMMENT "淋巴结-功能性右颈部-癌转移枚数",
  `lbj_gnxyjb_lbjzdj`  varchar(10)   NULL  COMMENT "淋巴结-功能性右颈部-淋巴结最大径（mm）",
  `lbj_gnxyjb   ene`  varchar(2)   NULL  COMMENT "淋巴结-功能性右颈部-ENE（0:无 1:有）",
  `fzjc_myzh`  varchar(500)   NULL  COMMENT "辅助检查-免疫组化",
  `fzjc_eberywzj`  varchar(2)   NULL  COMMENT "辅助检查-EBER原位杂交（1:阳性 2:阴性）",
  `fzjc_hpv`  varchar(100)   NULL  COMMENT "辅助检查-HPV",
  `fzjc_fzblxm`  varchar(100)   NULL  COMMENT "辅助检查-分子病理项目",
  `fzjc_fzbljg`  varchar(2000)   NULL  COMMENT "辅助检查-分子病理检测结果",
  `fzjc_lsj`  varchar(2000)   NULL  COMMENT "辅助检查-另送检",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_病理报告';
-- 喉癌_入院记录-个人史
DROP TABLE IF EXISTS coc_zy_hbzl_ryjl_grs;
CREATE TABLE `coc_zy_hbzl_ryjl_grs` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `crbjcs`  varchar(2)   NULL  COMMENT "个人史-传染病接触史（1:有 0:无）",
  `xys`  varchar(2)   NULL  COMMENT "个人史-吸烟史（1:有 0:无）",
  `xys_xyns`  varchar(2)   NULL  COMMENT "个人史-吸烟史-吸烟年数（年）",
  `xys_mrxyl`  varchar(2)   NULL  COMMENT "个人史-吸烟史-每日吸烟量（支）",
  `xys_jy`  varchar(2)   NULL  COMMENT "个人史-吸烟史-戒烟（1:已戒烟 0:未戒烟）",
  `xys_jyns`  varchar(2)   NULL  COMMENT "个人史-吸烟史-戒烟年数（年； 未戒烟填0）",
  `yjs`  varchar(2)   NULL  COMMENT "个人史-饮酒史（1:有 0:无）",
  `yjs_yjns`  varchar(2)   NULL  COMMENT "个人史-饮酒史-饮酒年数（年）",
  `yjs_pjmryjl`  varchar(4)   NULL  COMMENT "个人史-饮酒史-平均每日饮酒量（ml）",
  `yjs_sfjj`  varchar(2)   NULL  COMMENT "个人史-饮酒史-戒酒（0:未戒酒 1:未戒酒，但已已明显减少饮酒2:已戒酒）",
  `yjs_xjjjns`  varchar(2)   NULL  COMMENT "个人史-饮酒史-戒酒或明显减少饮酒年数（年； 未戒酒填0）",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_入院记录-个人史';
-- 喉癌_放疗小结-放射治疗剂量
DROP TABLE IF EXISTS coc_zy_hbzl_flxj_fszljl;
CREATE TABLE `coc_zy_hbzl_flxj_fszljl` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `fllx`  varchar(2)   NULL  COMMENT "放疗类型（1:根治性放疗 2:同步放化疗 3:术前放疗 4:术后放疗 5:姑息性放疗 6:其他）",
  `fljs`  varchar(2)   NULL  COMMENT "放疗技术（1:调强放疗（VMAT）2:调强放疗（IMRT）3:三维适形 4:二维5:立体定向放疗（SBRT））",
  `cf`  varchar(10)   NULL  COMMENT "处方",
  `jq`  varchar(100)   NULL  COMMENT "机器",
  `nl`  varchar(10)   NULL  COMMENT "能量",
  `bq`  varchar(10)   NULL  COMMENT "靶区",
  `cjl`  varchar(5)   NULL  COMMENT "次剂量（cGy/次）",
  `cs`  varchar(2)   NULL  COMMENT "次数",
  `zl`  varchar(6)   NULL  COMMENT "总量（cGy）",
  `fgfs`  varchar(10)   NULL  COMMENT "分割方式",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_放疗小结-放射治疗剂量';
-- 喉癌_影像报告
DROP TABLE IF EXISTS coc_zy_hbzl_yxbg;
CREATE TABLE `coc_zy_hbzl_yxbg` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `kh`  varchar(32)   NOT NULL  COMMENT "卡号（患者就诊卡卡号）",
  `klx`  varchar(16)   NOT NULL  COMMENT "卡类型（参见字典表）",
  `xgbz`  varchar(1)   NOT NULL  COMMENT "修改标志（1:正常 2:修改3:撤销）",
  `yjlxh`  varchar(32)   NOT NULL  COMMENT "原纪录序号（院内唯一标识）",
  `zkwz`  varchar(2)   NULL  COMMENT "检查所见-肿块位置（1:声门2:声门上3:声门下）",
  `zkpx`  varchar(2)   NULL  COMMENT "检查所见-肿块偏向（1:偏左侧2:偏右侧）",
  `zldx_length`  varchar(4)   NULL  COMMENT "检查所见-肿瘤大小-长（肿瘤大小： ** cm）",
  `zldx_width`  varchar(4)   NULL  COMMENT "检查所见-肿瘤大小-宽",
  `zldx_height`  varchar(4)   NULL  COMMENT "检查所见-肿瘤大小-高",
  `zlqh_cd`  varchar(2)   NULL  COMMENT "肿瘤强化-强化程度（1:轻度 2:中度 3:显著）",
  `zlqh_jy`  varchar(2)   NULL  COMMENT "肿瘤强化-均匀（1:均匀 0:不均匀）",
  `zlqh_nbhsq`  varchar(2)   NULL  COMMENT "肿瘤强化-囊变或坏死区（1:可见 2:未见）",
  `pljglj_hy`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-会厌（1:累及 0:未累及）",
  `pljglj_hyqjx`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-会厌前间隙（1:累及 0:未累及）",
  `pljglj_sg`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-舌根（1:累及 0:未累及）",
  `pljglj_hpzl`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-会披皱襞（0:未累及 1:左侧2:右侧 3:双侧）",
  `pljglj_pl`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-披裂（0:未累及 1:左侧2:右侧 3:双侧）",
  `pljglj_shd`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-室带（0:未累及 1:左侧2:右侧 3:双侧）",
  `pljglj_sd`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-声带（0:未累及 1:左侧2:右侧 3:双侧）",
  `pljglj_qlh`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-前联合（1:累及 0:未累及）",
  `pljglj_smx`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-声门下（1:累及 0:未累及）",
  `pljglj_hpjx`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-喉旁间隙（0:未累及 1:左侧2:右侧 3:双侧）",
  `pljglj_ycb`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-咽侧壁（0:未累及 1:左侧2:右侧 3:双侧）",
  `pljglj_lzw`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-梨状窝（0:未累及 1:左侧2:右侧 3:双侧）",
  `pljglj_yhb`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-咽后壁（1:累及 0:未累及）",
  `pljglj_hhq`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-环后区（1:累及 0:未累及）",
  `pljglj_jzrg`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-甲状软骨（1:累及 0:未累及）",
  `pljglj_hzrg`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-环状软骨（1:累及 0:未累及）",
  `pljglj_hwzz`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-喉外组织（1:累及 0:未累及）",
  `pljglj_dzj`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-带状肌（0:未累及 1:左侧2:右侧 3:双侧）",
  `pljglj_jzx`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-甲状腺（0:未累及 1:左侧2:右侧 3:双侧）",
  `pljglj_shg`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-食管（1:累及 0:未累及）",
  `pljglj_qg`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-气管（1:累及 0:未累及）",
  `pljglj_zqjx`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-椎前间隙（1:累及 0:未累及）",
  `pljglj_zg`  varchar(2)   NULL  COMMENT "毗邻结构可见肿瘤累及-纵隔（1:累及 0:未累及）",
  `lbjzd_zj`  varchar(2)   NULL  COMMENT "淋巴结肿大-左颈（0:无 1:咽后 2:I区 3:IIA区 4:IIB区 5:III区 6:IV区 7:V区 8:VI区9:VII区）",
  `lbjzd_yj`  varchar(2)   NULL  COMMENT "淋巴结肿大-右颈（0:无 1:咽后 2:I区 3:IIA区 4:IIB区 5:III区 6:IV区 7:V区 8:VI区9:VII区）",
  `lbjzd_lbjzdz_length`  varchar(4)   NULL  COMMENT "淋巴结肿大-淋巴结最大者-长（淋巴结最大者：** cm）",
  `lbjzd_lbjzdz_width`  varchar(4)   NULL  COMMENT "淋巴结肿大-淋巴结最大者-宽",
  `lbjzd_lbjzdz_height`  varchar(4)   NULL  COMMENT "淋巴结肿大-淋巴结最大者-高",
  `lbjzd_zdzqy`  varchar(20)   NULL  COMMENT "淋巴结肿大-淋巴结最大者-区域",
  `lbjzd_rh`  varchar(2)   NULL  COMMENT "是否融合（1:是 0:否）",
  `zlbr_jzdm`  varchar(2)   NULL  COMMENT "以下血管结构可见肿瘤包饶-颈总动脉（1:是 0:否）",
  `zlbr_jndm`  varchar(2)   NULL  COMMENT "肿瘤包饶-颈内动脉（1:是 0:否）",
  `zlbr_jwdm`  varchar(2)   NULL  COMMENT "肿瘤包饶-颈外动脉（1:是 0:否）",
  `zlbr_jnjm`  varchar(2)   NULL  COMMENT "肿瘤包饶-颈内静脉（1:是 0:否）",
  `zlbr_jwjm`  varchar(2)   NULL  COMMENT "肿瘤包饶-颈外静脉（1:是 0:否）",
  `zlxthsy_jzdm`  varchar(2)   NULL  COMMENT "以下血管结构可见与肿瘤相贴或受压-颈总动脉（1:是 0:否）",
  `zlxthsy_jndm`  varchar(2)   NULL  COMMENT "肿瘤相贴或受压-颈内动脉（1:是 0:否）",
  `zlxthsy_jwdm`  varchar(2)   NULL  COMMENT "肿瘤相贴或受压-颈外动脉（1:是 0:否）",
  `zlxthsy_jnjm`  varchar(2)   NULL  COMMENT "肿瘤相贴或受压-颈内静脉（1:是 0:否）",
  `zlxthsy_jwjm`  varchar(2)   NULL  COMMENT "肿瘤相贴或受压-颈外静脉（1:是 0:否）",
  `jcjl`  varchar(2000)   NULL  COMMENT "检查结论",
  `blbjzy`  varchar(2)   NULL  COMMENT "伴淋巴结转移（1:有  0:无）",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_影像报告';
-- 喉癌_手术记录
DROP TABLE IF EXISTS coc_zy_hbzl_ssjl;
CREATE TABLE `coc_zy_hbzl_ssjl` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `kh`  varchar(32)   NOT NULL  COMMENT "卡号（患者就诊卡卡号）",
  `klx`  varchar(16)   NOT NULL  COMMENT "卡类型（参见字典表）",
  `xgbz`  varchar(1)   NOT NULL  COMMENT "修改标志（1:正常 2:修改3:撤销）",
  `yjlxh`  varchar(32)   NOT NULL  COMMENT "原纪录序号（院内唯一标识）",
  `hzxm`  varchar(50)   NULL  COMMENT "姓名",
  `hzxb`  varchar(10)   NULL  COMMENT "性别（参考字典）",
  `hznl`  varchar(10)   NULL  COMMENT "年龄",
  `ssrq`  varchar(20)   NULL  COMMENT "手术日期",
  `sqzd`  varchar(100)   NULL  COMMENT "术前诊断",
  `szzd`  varchar(100)   NULL  COMMENT "术中诊断",
  `ssmc`  varchar(100)   NULL  COMMENT "手术名称",
  `sslx`  varchar(2)   NULL  COMMENT "手术类型（1:喉癌CHEP手术;2:喉癌垂直半喉手术; 3:喉癌根治性劲清扫术 4:喉癌功能性劲清扫术 5:喉癌全喉切除术 6: 喉癌水平半喉手术）",
  `zdys`  varchar(50)   NULL  COMMENT "主刀医师",
  `dyzs`  varchar(50)   NULL  COMMENT "第一助手",
  `dezs`  varchar(50)   NULL  COMMENT "第二助手",
  `mzfs`  varchar(50)   NULL  COMMENT "麻醉方式",
  `mzys`  varchar(50)   NULL  COMMENT "麻醉医师",
  `ssjg`  varchar(2000)   NULL  COMMENT "手术经过",
  `ssysqm`  varchar(50)   NULL  COMMENT "手术医师签名",
  `ssysqms`  varchar(20)   NULL  COMMENT "手术医师签名日期（年月日时分）",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_手术记录';
-- 喉癌_随访记录
DROP TABLE IF EXISTS coc_zy_hbzl_sfjl;
CREATE TABLE `coc_zy_hbzl_sfjl` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `kh`  varchar(32)   NOT NULL  COMMENT "卡号（患者就诊卡卡号）",
  `klx`  varchar(16)   NOT NULL  COMMENT "卡类型（参见字典表）",
  `xgbz`  varchar(1)   NOT NULL  COMMENT "修改标志（1:正常 2:修改3:撤销）",
  `yjlxh`  varchar(32)   NOT NULL  COMMENT "原纪录序号（院内唯一标识）",
  `xm`  varchar(50)   NULL  COMMENT "姓名",
  `xb`  varchar(10)   NULL  COMMENT "性别",
  `nl`  varchar(10)   NULL  COMMENT "年龄",
  `jg`  varchar(100)   NULL  COMMENT "籍贯",
  `mz`  varchar(50)   NULL  COMMENT "民族",
  `csd`  varchar(100)   NULL  COMMENT "出生地",
  `hy`  varchar(10)   NULL  COMMENT "婚姻",
  `zy`  varchar(20)   NULL  COMMENT "职业",
  `bscsz`  varchar(50)   NULL  COMMENT "病史陈述者",
  `jlrq`  varchar(20)   NULL  COMMENT "记录日期",
  `zs`  varchar(2000)   NULL  COMMENT "主诉",
  `bsms_haqcssjj`  varchar(20)   NULL  COMMENT "病史描述-喉癌切除手术距今（【天/月/年】前）",
  `bsms_jblbjqss`  varchar(2)   NULL  COMMENT "病史描述-颈淋巴结清扫术（0:无 1:有）",
  `bsms_shbl`  varchar(500)   NULL  COMMENT "病史描述-术后病理",
  `bsms_hj_jcsj`  varchar(20)   NULL  COMMENT "病史描述-喉镜-检查时间",
  `bsms_hj_jcdw`  varchar(2)   NULL  COMMENT "病史描述-喉镜-检查单位（1:我院 2:外院）",
  `bsms_hj_jcbg`  varchar(500)   NULL  COMMENT "病史描述-喉镜-检查报告",
  `bsms_jbzqct_jcsj`  varchar(20)   NULL  COMMENT "病史描述-颈部增强CT-检查时间",
  `bsms_jbzqct_jcdw`  varchar(2)   NULL  COMMENT "病史描述-颈部增强CT-检查单位（1:我院 2:外院）",
  `bsms_jbzqct_jcbg`  varchar(500)   NULL  COMMENT "病史描述-颈部增强CT-检查报告",
  `jws_ywgms`  varchar(2)   NULL  COMMENT "既往史-药物过敏史（0:无 1:有）",
  `tgjc_yb`  varchar(2)   NULL  COMMENT "体格检查-咽部（0:不正常 1:正常）",
  `tgjc_jjhjxjhy`  varchar(2)   NULL  COMMENT "体格检查-间接喉镜下见会厌（0:不正常 1:正常）",
  `tgjc_zcsd`  varchar(2)   NULL  COMMENT "体格检查-左侧声带（0:不正常 1:正常）",
  `tgjc_ycsd`  varchar(2)   NULL  COMMENT "体格检查-右侧声带（0:不正常 1:正常）",
  `tgjc_zcshd`  varchar(2)   NULL  COMMENT "体格检查-左侧室带（0:不正常 1:正常）",
  `tgjc_ycshd`  varchar(2)   NULL  COMMENT "体格检查-右侧室带（0:不正常 1:正常）",
  `tgjc_jbzdlbj`  varchar(2)   NULL  COMMENT "体格检查-颈部肿大淋巴结（0:未扪及 1:扪及）",
  `tgjc_zlkqk`  varchar(500)   NULL  COMMENT "体格检查-造瘘口情况",
  `qspg_sypg`  varchar(2)   NULL  COMMENT "嗓音评估（0:否 1:是）",
  `qspg_sypgjg`  varchar(500)   NULL  COMMENT "嗓音评估结果",
  `qspg_typg`  varchar(2)   NULL  COMMENT "吞咽评估（0:否 1:是）",
  `qspg_typgjg`  varchar(500)   NULL  COMMENT "吞咽评估结果",
  `cbzd`  varchar(100)   NULL  COMMENT "初步诊断",
  `cl`  varchar(500)   NULL  COMMENT "处理",
  `hj_jcsj`  varchar(20)   NULL  COMMENT "喉镜-检查时间",
  `hj_jcdw`  varchar(100)   NULL  COMMENT "喉镜-检查单位",
  `hj_jcjg`  varchar(500)   NULL  COMMENT "喉镜-检查结果",
  `jbzqct_jcsj`  varchar(20)   NULL  COMMENT "颈部增强CT-检查时间",
  `jbzqct_jcdw`  varchar(100)   NULL  COMMENT "颈部增强CT-检查单位",
  `jbzqct_jcjg`  varchar(500)   NULL  COMMENT "颈部增强CT-检查结果",
  `hgnpg`  varchar(500)   NULL  COMMENT "喉功能评估",
  `zhzlsj`  varchar(20)   NULL  COMMENT "综合治疗时间（【天/月/年】后）",
  `zhzlfa`  varchar(500)   NULL  COMMENT "综合治疗方案",
  `sxz`  varchar(50)   NULL  COMMENT "书写者",
  `cjsj`  varchar(20)   NULL  COMMENT "创建时间",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_随访记录';
-- 喉癌_入院记录（放疗）-辅助检查
DROP TABLE IF EXISTS coc_zy_hbzl_ryjlfl_fzjc;
CREATE TABLE `coc_zy_hbzl_ryjlfl_fzjc` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `ywdzhjjc`  varchar(2)   NULL  COMMENT "辅助检查-电子喉镜检查-有无（1:有 0:无）",
  `dzhjjc_yymc`  varchar(50)   NULL  COMMENT "辅助检查-电子喉镜检查-医院名称",
  `ywdzhjjc_jcsj`  varchar(20)   NULL  COMMENT "辅助检查-电子喉镜检查-检查时间",
  `dzhjjc_jcjg`  varchar(500)   NULL  COMMENT "辅助检查-电子喉镜检查-检查结果",
  `ywjbzqctmri`  varchar(2)   NULL  COMMENT "辅助检查-颈部增强CT/MRI-有无（1:有 0:无）",
  `jbzqctmri_yymc`  varchar(50)   NULL  COMMENT "辅助检查-颈部增强CT/MRI-医院名称",
  `jbzqctmri_jcsj`  varchar(20)   NULL  COMMENT "辅助检查-颈部增强CT/MRI-检查时间",
  `jbzqctmri_jch`  varchar(20)   NULL  COMMENT "辅助检查-颈部增强CT/MRI-检查号",
  `jbzqctmri_jcjg`  varchar(500)   NULL  COMMENT "辅助检查-颈部增强CT/MRI-检查结果",
  `ywxbctjc`  varchar(2)   NULL  COMMENT "辅助检查-胸部CT检查-有无（1:有 0:无）",
  `xbctjc_yymc`  varchar(50)   NULL  COMMENT "辅助检查-胸部CT检查-医院名称",
  `xbctjc_jcsj`  varchar(20)   NULL  COMMENT "辅助检查-胸部CT检查-检查时间",
  `xbctjc_jch`  varchar(20)   NULL  COMMENT "辅助检查-胸部CT检查-检查号",
  `xbctjc_jcjg`  varchar(500)   NULL  COMMENT "辅助检查-胸部CT检查-检查结果",
  `ywfbbcctjc`  varchar(2)   NULL  COMMENT "辅助检查-腹部B超/CT检查-有无（1:有 0:无）",
  `fbbcctjc_yymc`  varchar(50)   NULL  COMMENT "辅助检查-腹部B超/CT检查-医院名称",
  `fbbcctjc_jcsj`  varchar(20)   NULL  COMMENT "辅助检查-腹部B超/CT检查-检查时间",
  `fbbcctjc_jch`  varchar(20)   NULL  COMMENT "辅助检查-腹部B超/CT检查-检查号",
  `fbbcctjc_jcjg`  varchar(500)   NULL  COMMENT "辅助检查-腹部B超/CT检查-检查结果",
  `ywjbbc`  varchar(2)   NULL  COMMENT "辅助检查-颈部B超-有无（1:有 0:无）",
  `jbbc_yymc`  varchar(50)   NULL  COMMENT "辅助检查-颈部B超-医院名称",
  `jbbc_jcsj`  varchar(20)   NULL  COMMENT "辅助检查-颈部B超-检查时间",
  `jbbc_jch`  varchar(20)   NULL  COMMENT "辅助检查-颈部B超-检查号",
  `jbbc_jcjg`  varchar(500)   NULL  COMMENT "辅助检查-颈部B超-检查结果",
  `ywxdt`  varchar(2)   NULL  COMMENT "辅助检查-心电图（1:有 0:无）",
  `xdt_jcjl`  varchar(100)   NULL  COMMENT "辅助检查-心电图-检查结论",
  `ywgsmjc`  varchar(2)   NULL  COMMENT "辅助检查-骨扫描检查-有无（1:有 0:无）",
  `gsmjc_yymc`  varchar(50)   NULL  COMMENT "辅助检查-骨扫描检查-医院名称",
  `gsmjc_jcsj`  varchar(20)   NULL  COMMENT "辅助检查-骨扫描检查-检查时间",
  `gsmjc_jch`  varchar(20)   NULL  COMMENT "辅助检查-骨扫描检查-检查号",
  `gsmjc_jcjg`  varchar(500)   NULL  COMMENT "辅助检查-骨扫描检查-检查结果",
  `ywzzblxjc`  varchar(2)   NULL  COMMENT "辅助检查-组织病理学检查-有无（1:有 0:无）",
  `zzblxjc_`  varchar(50)   NULL  COMMENT "辅助检查-组织病理学检查-医院名称",
  `zzblxjc_jcsj`  varchar(20)   NULL  COMMENT "辅助检查-组织病理学检查-检查时间",
  `zzblxjc_blh`  varchar(20)   NULL  COMMENT "辅助检查-组织病理学检查-病理号",
  `zzblxjc_jcjg`  varchar(500)   NULL  COMMENT "辅助检查-组织病理学检查-检查结果",
  `ywpetctjc`  varchar(2)   NULL  COMMENT "辅助检查-PET-CT检查-有无（1:有 0:无）",
  `petctjc_yymc`  varchar(50)   NULL  COMMENT "辅助检查-PET-CT检查-医院名称",
  `petctjc_jcsj`  varchar(20)   NULL  COMMENT "辅助检查-PET-CT检查-检查时间",
  `petctjc_jch`  varchar(20)   NULL  COMMENT "辅助检查-PET-CT检查-检查号",
  `petctjc_jcjg`  varchar(500)   NULL  COMMENT "辅助检查-PET-CT检查-检查结果",
  `ywygbdjc`  varchar(2)   NULL  COMMENT "辅助检查-乙肝病毒-有无（1:有 0:无）",
  `ygbdjc_yymc`  varchar(50)   NULL  COMMENT "辅助检查-乙肝病毒-医院名称",
  `ygbdjc_jcsj`  varchar(20)   NULL  COMMENT "辅助检查-乙肝病毒-检查时间",
  `ygbdjc_jcjg`  varchar(500)   NULL  COMMENT "辅助检查-乙肝病毒-检查结果",
  `qtjc`  varchar(500)   NULL  COMMENT "辅助检查-其他",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_入院记录（放疗）-辅助检查';
-- 喉癌_入院记录（放疗）-个人史
DROP TABLE IF EXISTS coc_zy_hbzl_ryjlfl_grs;
CREATE TABLE `coc_zy_hbzl_ryjlfl_grs` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `crbjcs`  varchar(100)   NULL  COMMENT "个人史-出生地",
  `ywyyjcs`  varchar(2)   NULL  COMMENT "个人史-疫源接触史（1:有 0:无）",
  `yyjcs_yqmc`  varchar(100)   NULL  COMMENT "个人史-疫源接触史-疫区名称",
  `yyjcs_jcsj`  varchar(2)   NULL  COMMENT "个人史-疫源接触史-接触时间（年）",
  `ffjydhxwpfsxwzjcs`  varchar(2)   NULL  COMMENT "个人史-粉尘及有毒化学物品、放射性物质接触史（1:有 0:无）",
  `ffjydhxwpfsxwzjcs_jcsj`  varchar(10)   NULL  COMMENT "个人史-粉尘及有毒化学物品、放射性物质接触史-接触时间",
  `ffjydhxwpfsxwzjcs_jcdd`  varchar(100)   NULL  COMMENT "个人史-粉尘及有毒化学物品、放射性物质接触史-接触地点",
  `ffjydhxwpfsxwzjcs_jcwz`  varchar(100)   NULL  COMMENT "个人史-粉尘及有毒化学物品、放射性物质接触史-接触物质",
  `ywxys`  varchar(2)   NULL  COMMENT "个人史-吸烟史（1:有 0:无）",
  `xys_xyns`  varchar(2)   NULL  COMMENT "个人史-吸烟史-吸烟年数（年）",
  `xys_mrxyl`  varchar(2)   NULL  COMMENT "个人史-吸烟史-每日吸烟量（支）",
  `xys_jy`  varchar(2)   NULL  COMMENT "个人史-吸烟史-戒烟（1:已戒烟 0:未戒烟）",
  `xys_jyns`  varchar(2)   NULL  COMMENT "个人史-吸烟史-戒烟年数（年； 未戒烟填0）",
  `ywyjs`  varchar(2)   NULL  COMMENT "个人史-饮酒史（1:有 0:无）",
  `yjs_yjns`  varchar(2)   NULL  COMMENT "个人史-饮酒史-饮酒年数（年）",
  `yjs_zyyjzl`  varchar(2)   NULL  COMMENT "个人史-饮酒史-主要饮酒种类（1:白酒 2:啤酒3:红酒 4:黄酒）",
  `yjs_pjmryjl`  varchar(4)   NULL  COMMENT "个人史-饮酒史-平均每日饮酒量（ml）",
  `yjs_sfjj`  varchar(2)   NULL  COMMENT "个人史-饮酒史-戒酒（0:未戒酒 1:未戒酒，但已明显减少饮酒 2:已戒酒）",
  `yjs_xjjjns`  varchar(2)   NULL  COMMENT "个人史-饮酒史-戒酒或明显减少饮酒年数（年； 未戒酒填0）",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_入院记录（放疗）-个人史';
-- 喉癌_出院小结
DROP TABLE IF EXISTS coc_zy_hbzl_cyxj;
CREATE TABLE `coc_zy_hbzl_cyxj` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `kh`  varchar(32)   NOT NULL  COMMENT "卡号（患者就诊卡卡号）",
  `klx`  varchar(16)   NOT NULL  COMMENT "卡类型（参见字典表）",
  `xgbz`  varchar(1)   NOT NULL  COMMENT "修改标志（1:正常 2:修改3:撤销）",
  `yjlxh`  varchar(32)   NOT NULL  COMMENT "原纪录序号（院内唯一标识）",
  `rysj`  varchar(20)   NULL  COMMENT "入院时间",
  `cysj`  varchar(20)   NULL  COMMENT "出院时间",
  `ryzd`  varchar(100)   NULL  COMMENT "入院诊断",
  `cyzd`  varchar(100)   NULL  COMMENT "出院诊断",
  `rysqk_hzxm`  varchar(50)   NULL  COMMENT "入院时情况-患者姓名",
  `rysqk_hzxb`  varchar(10)   NULL  COMMENT "入院时情况-患者性别",
  `rysqk_hznl`  varchar(10)   NULL  COMMENT "入院时情况-患者年龄",
  `rysqk_zs`  varchar(500)   NULL  COMMENT "入院时情况-主诉",
  `rysqk_rysj`  varchar(20)   NULL  COMMENT "入院时情况-入院时间",
  `rysqk_zkjc`  varchar(500)   NULL  COMMENT "入院时情况-专科检查",
  `zljg`  varchar(2000)   NULL  COMMENT "诊疗经过",
  `tsjc`  varchar(2000)   NULL  COMMENT "特殊检查",
  `cysqk`  varchar(2000)   NULL  COMMENT "出院时情况",
  `cyyz`  varchar(2000)   NULL  COMMENT "出院医嘱",
  `sjys`  varchar(50)   NULL  COMMENT "上级医师",
  `zyys`  varchar(50)   NULL  COMMENT "住院医师",
  `xjsj`  varchar(20)   NULL  COMMENT "小结时间",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_出院小结';
-- 喉癌_入院记录-实验室与辅助检查
DROP TABLE IF EXISTS coc_zy_hbzl_ryjl_sysyfzjc;
CREATE TABLE `coc_zy_hbzl_ryjl_sysyfzjc` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `hkj_jcrq`  varchar(20)   NULL  COMMENT "喉窥镜-检查日期",
  `hkj_jcdw`  varchar(2)   NULL  COMMENT "喉窥镜-检查单位（1:我院 2:外院）",
  `hkj_hysm`  varchar(2)   NULL  COMMENT "喉窥镜-会厌舌面（1:光滑 2:粗糙3:溃疡 4:充血5:肿胀 6:囊肿样物 7:淋巴样物 8:新生物9:未暴露 10:其他）",
  `hkj_hyhm`  varchar(2)   NULL  COMMENT "喉窥镜-会厌喉面（1:光滑 2:粗糙3:溃疡 4:新生物 5:其他）",
  `hkj_zshd`  varchar(2)   NULL  COMMENT "喉窥镜-左室带（1:光滑 2:粗糙3:溃疡 4:充血5:肥厚 6:新生物 7:其他）",
  `hkj_yshd`  varchar(2)   NULL  COMMENT "喉窥镜-右室带（1:光滑 2:粗糙3:溃疡 4:充血5:肥厚 6:新生物 7:其他）",
  `hkj_zpl`  varchar(2)   NULL  COMMENT "喉窥镜-左披裂（1:光滑 2:粗糙3:溃疡 4:充血5:肿胀 6:囊肿样物 7:淋巴样物 8:新生物9:其他）",
  `hkj_ypl`  varchar(2)   NULL  COMMENT "喉窥镜-右披裂（1:光滑 2:粗糙3:溃疡 4:充血5:肿胀 6:囊肿样物 7:淋巴样物 8:新生物9:其他）",
  `hkj_zsd`  varchar(2)   NULL  COMMENT "喉窥镜-左声带（1:光滑 2:粗糙3:急性充血 4:慢性充血 5:出血 6:肿胀 7:肥厚 8:小结9:息肉样物10:囊肿样物11:白斑样物12:肉芽样物13:新生物 14:活动好 15:活动受限 20:固定 17:其他）",
  `hkj_ysd`  varchar(2)   NULL  COMMENT "喉窥镜-右声带（1:光滑 2:粗糙3:急性充血 4:慢性充血 5:出血 6:肿胀 7:肥厚 8:小结9:息肉样物10:囊肿样物11:白斑样物12:肉芽样物13:新生物 14:活动好 15:活动受限 20:固定 17:其他）",
  `hkj_zlzw`  varchar(2)   NULL  COMMENT "喉窥镜-左梨状窝（1:光滑 2:异物3:新生物 4:积液 5:淋巴样组织 6:其他）",
  `hkj_ylzw`  varchar(2)   NULL  COMMENT "喉窥镜-右梨状窝（1:光滑 2:异物3:新生物 4:积液 5:淋巴样组织 6:其他）",
  `hkj_qt`  varchar(200)   NULL  COMMENT "喉窥镜-其他",
  `xwdzhj_jcrq`  varchar(20)   NULL  COMMENT "纤维电子喉镜-检查日期",
  `xwdzhj_jcdw`  varchar(2)   NULL  COMMENT "纤维电子喉镜-检查单位（1:我院 2:外院）",
  `hbzqct_jcrq`  varchar(20)   NULL  COMMENT "喉部增强CT-检查日期",
  `hbzqct_jcdw`  varchar(2)   NULL  COMMENT "喉部增强CT-检查单位（1:我院 2:外院）",
  `hbzqct_cth`  varchar(20)   NULL  COMMENT "喉部增强CT-CT号",
  `hbzqct_jcbg`  varchar(500)   NULL  COMMENT "喉部增强CT-检查报告",
  `hbzqmri_jcrq`  varchar(20)   NULL  COMMENT "喉部增强MRI-检查日期",
  `hbzqmri_jcdw`  varchar(2)   NULL  COMMENT "喉部增强MRI-检查单位（1:我院 2:外院）",
  `hbzqmri_mrih`  varchar(20)   NULL  COMMENT "喉部增强MRI-MRI号",
  `hbzqmri_jcbg`  varchar(500)   NULL  COMMENT "喉部增强MRI-检查报告",
  `blbg_jcrq`  varchar(20)   NULL  COMMENT "病理报告-检查日期",
  `blbg_jcdw`  varchar(2)   NULL  COMMENT "病理报告-检查单位（1:我院 2:外院3:我院会诊外片）",
  `blbg_blh`  varchar(20)   NULL  COMMENT "病理报告-病理号",
  `blbg_bgnr`  varchar(500)   NULL  COMMENT "病理报告-报告内容",
  `xbzwp_jcrq`  varchar(20)   NULL  COMMENT "胸部正位片-检查日期",
  `xbzwp_jcdw`  varchar(2)   NULL  COMMENT "胸部正位片-检查单位（1:我院 2:外院）",
  `xbzwp_xxh`  varchar(20)   NULL  COMMENT "胸部正位片-X线号",
  `xbzwp_jcjl`  varchar(200)   NULL  COMMENT "胸部正位片-检查结论",
  `sdbcts_jcrq`  varchar(20)   NULL  COMMENT "食道钡餐透视-检查日期",
  `sdbcts_jcdw`  varchar(2)   NULL  COMMENT "食道钡餐透视-检查单位（1:我院 2:外院）",
  `sdbcts_jcbg`  varchar(500)   NULL  COMMENT "食道钡餐透视-检查报告",
  `xdt_jcrq`  varchar(20)   NULL  COMMENT "心电图-检查日期",
  `xdt_jcdw`  varchar(2)   NULL  COMMENT "心电图-检查单位（1:我院 2:外院）",
  `xdt_jcjl`  varchar(200)   NULL  COMMENT "心电图-检查结论",
  `sqcghy_hyxm`  varchar(200)   NULL  COMMENT "术前常规化验-化验项目",
  `sqcghy_hyrq`  varchar(20)   NULL  COMMENT "术前常规化验-化验日期",
  `sqcghy_hydw`  varchar(2)   NULL  COMMENT "术前常规化验-化验单位（1:我院 2:外院）",
  `sqcghy_hyjl`  varchar(200)   NULL  COMMENT "术前常规化验-化验结论",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_入院记录-实验室与辅助检查';
-- 喉癌_入院记录-月经史
DROP TABLE IF EXISTS coc_zy_hbzl_ryjl_yjs;
CREATE TABLE `coc_zy_hbzl_ryjl_yjs` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `yjs_yw`  varchar(2)   NULL  COMMENT "月经史-有无（0:无 1:有 2:已绝经）",
  `yjs_ccnl`  varchar(2)   NULL  COMMENT "月经史-初潮年龄（岁）",
  `yjs_yjzq`  varchar(2)   NULL  COMMENT "月经史-月经周期（0:不规则 1:规则）",
  `yjs_yjl`  varchar(2)   NULL  COMMENT "月经史-月经量（1:中等 2:多3:少）",
  `yjs_xkytj`  varchar(2)   NULL  COMMENT "月经史-血块和痛经（0:无血块、无痛经 1:有血块、无痛经 2:无血块、有痛经 3:有血块、有痛经）",
  `yjs_mcyjsj`  varchar(20)   NULL  COMMENT "月经史-末次月经时间（年月日）",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_入院记录-月经史';
-- 喉癌_门诊MDT记录
DROP TABLE IF EXISTS coc_zy_hbzl_mzmdtjl;
CREATE TABLE `coc_zy_hbzl_mzmdtjl` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `kh`  varchar(32)   NOT NULL  COMMENT "卡号（患者就诊卡卡号）",
  `klx`  varchar(16)   NOT NULL  COMMENT "卡类型（参见字典表）",
  `xgbz`  varchar(1)   NOT NULL  COMMENT "修改标志（1:正常 2:修改3:撤销）",
  `yjlxh`  varchar(32)   NOT NULL  COMMENT "原纪录序号（院内唯一标识）",
  `tlsj`  varchar(20)   NULL  COMMENT "讨论时间",
  `fqks`  varchar(50)   NULL  COMMENT "发起科室",
  `cyry`  varchar(1000)   NULL  COMMENT "参与人员",
  `cyks`  varchar(1000)   NULL  COMMENT "参与科室",
  `hzjbqk`  varchar(500)   NULL  COMMENT "患者基本情况",
  `fzjc`  varchar(500)   NULL  COMMENT "辅助检查",
  `cbzd`  varchar(100)   NULL  COMMENT "初步诊断",
  `cl`  varchar(500)   NULL  COMMENT "处理",
  `tlmd`  varchar(500)   NULL  COMMENT "讨论目的",
  `tljg_blk_ysxm`  varchar(50)   NULL  COMMENT "讨论经过-病理科-医师姓名",
  `tljg_blk_bljg`  varchar(500)   NULL  COMMENT "讨论经过-病理科-病理结果",
  `tljg_blk_blfx`  varchar(100)   NULL  COMMENT "讨论经过-病理科-病理分型",
  `tljg_fsk_ysxm`  varchar(50)   NULL  COMMENT "讨论经过-放射科-医师姓名",
  `tljg_fsk_jtzlfw`  varchar(500)   NULL  COMMENT "讨论经过-放射科-具体肿瘤范围",
  `tljg_fhlk_ysxm`  varchar(50)   NULL  COMMENT "讨论经过-放化疗科-医师姓名",
  `tljg_fhlk_fhllx`  varchar(2)   NULL  COMMENT "讨论经过-放化疗科-放化疗类型（1:诱导 2:补充 3:放疗 4:化疗）",
  `tljg_fhlk_jtfhlfa`  varchar(500)   NULL  COMMENT "讨论经过-放化疗科-具体放化疗方案",
  `tljg_ebhkyk_ysxm`  varchar(50)   NULL  COMMENT "讨论经过-耳鼻喉科/眼科-医师",
  `tljg_ebhkyk_jtssfa`  varchar(500)   NULL  COMMENT "讨论经过-耳鼻喉科/眼科-具体手术方案",
  `tljg`  varchar(2000)   NULL  COMMENT "讨论结果",
  `xybzlfa_zllx`  varchar(2)   NULL  COMMENT "下一步治疗方案-治疗类型（1:手术 2:放疗 3:化疗 4:姑息治疗 5:放疗+免疫 6:单免疫评估或随访 7:靶向）",
  `xybzlfa_jtfa`  varchar(2000)   NULL  COMMENT "下一步治疗方案-具体方案",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_门诊MDT记录';
-- 喉癌_入院记录-专科检查
DROP TABLE IF EXISTS coc_zy_hbzl_ryjl_zkjc;
CREATE TABLE `coc_zy_hbzl_ryjl_zkjc` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `bb_wb_jx`  varchar(2)   NULL  COMMENT "鼻-外鼻-畸形（0:无畸形 1:鼻梁略向左偏 2:鼻梁略向右偏3:酒渣鼻）",
  `bb_bzg_pq`  varchar(2)   NULL  COMMENT "鼻-鼻中隔-偏曲（0:居中，无明显偏曲 1:向左偏曲 2:向右偏曲 3:S形偏曲4:前端可见穿孔 5:C形偏曲）",
  `bb_bzg_tq`  varchar(2)   NULL  COMMENT "鼻-鼻中隔-突起（0:无明显突起1:可见棘突 2:可见嵴突 3:可见矩状突）",
  `bb_bj`  varchar(2)   NULL  COMMENT "鼻-鼻甲（0:无肿大 1:双侧下鼻甲大 2:左侧下鼻甲大3:右侧下鼻甲大）",
  `bb_yb_xr`  varchar(2)   NULL  COMMENT "鼻-右鼻-息肉（0:无息肉 1:息肉局限于中鼻道 2:息肉超出中鼻道）",
  `bb_yb_sz`  varchar(2)   NULL  COMMENT "鼻-右鼻-水肿（0:无 1:轻度2:严重）",
  `bb_yb_fmw`  varchar(2)   NULL  COMMENT "鼻-右鼻-分泌物（0:无 1:清亮、稀薄 2:粘稠、脓性）",
  `bb_zb_xr`  varchar(2)   NULL  COMMENT "鼻-左鼻-息肉（0:无息肉 1:息肉局限于中鼻道 2:息肉超出中鼻道）",
  `bb_zb_sz`  varchar(2)   NULL  COMMENT "鼻-左鼻-水肿（0:无 1:轻度2:严重）",
  `bb_zb_fmw`  varchar(2)   NULL  COMMENT "鼻-左鼻-分泌物（0:无 1:清亮、稀薄 2:粘稠、脓性）",
  `yb_by`  varchar(2)   NULL  COMMENT "咽-鼻咽（0:未窥及 1:光滑 2:充血 3:新生物 4:溃疡5:出血 6:淋巴组织增生）",
  `yb_ky_chx`  varchar(2)   NULL  COMMENT "咽-口咽-充血（1:是  0:否）",
  `yb_ky_btt`  varchar(2)   NULL  COMMENT "咽-口咽-扁桃体（0:无肿大 1:有肿大，I ° 2:有肿大，II °3:有肿大，III ° 4:有肿大， III °+）",
  `yb_ky_sc`  varchar(2)   NULL  COMMENT "咽-口咽-渗出（0:无 1:有）",
  `yb_ky_ky`  varchar(2)   NULL  COMMENT "咽-口咽-溃疡（0:无 1:有）",
  `yb_ky_wm`  varchar(2)   NULL  COMMENT "咽-口咽-伪膜（0:无 1:有）",
  `yb_ky_cx`  varchar(2)   NULL  COMMENT "咽-口咽-出血（0:无 1:有）",
  `yb_ky_zcbttxsw_yw`  varchar(2)   NULL  COMMENT "咽-口咽-左侧扁桃体新生物（0:无 1:有）",
  `yb_ky_zcbttxsw_xt`  varchar(2)   NULL  COMMENT "咽-口咽-左侧扁桃体新生物-形态（1:菜花型 2:结节或包块型 3:溃疡浸润型 4:混合型）",
  `yb_ky_zcbttxsw_bj`  varchar(2)   NULL  COMMENT "咽-口咽-左侧扁桃体新生物-边界（1:不清 1:清）",
  `yb_ky_zcbttxsw_bmgh`  varchar(2)   NULL  COMMENT "咽-口咽-左侧扁桃体新生物-表面光滑（0:否 1:是）",
  `yb_ky_zcbttxsw_bmkp`  varchar(2)   NULL  COMMENT "咽-口咽-左侧扁桃体新生物-表面溃破（0:无 1:有）",
  `yb_ky_zcbttxsw_dx_length`  varchar(6)   NULL  COMMENT "咽-口咽-左侧扁桃体新生物-大小-长（cm）",
  `yb_ky_zcbttxsw_dx_width`  varchar(6)   NULL  COMMENT "咽-口咽-左侧扁桃体新生物-大小-宽（cm）",
  `yb_ky_ycbttxsw_yw`  varchar(2)   NULL  COMMENT "咽-口咽-右侧扁桃体新生物（0:无 1:有）",
  `yb_ky_ycbttxsw_xt`  varchar(2)   NULL  COMMENT "咽-口咽-右侧扁桃体新生物-形态（1:菜花型 2:结节或包块型 3:溃疡浸润型 4:混合型）",
  `yb_ky_ycbttxsw_bj`  varchar(2)   NULL  COMMENT "咽-口咽-右侧扁桃体新生物-边界（1:不清 1:清）",
  `yb_ky_ycbttxsw_bmgh`  varchar(2)   NULL  COMMENT "咽-口咽-右侧扁桃体新生物-表面光滑（0:否 1:是）",
  `yb_ky_ycbttxsw_bmkp`  varchar(2)   NULL  COMMENT "咽-口咽-右侧扁桃体新生物-表面溃破（0:无 1:有）",
  `yb_ky_ycbttxsw_dx_length`  varchar(6)   NULL  COMMENT "咽-口咽-右侧扁桃体新生物-大小-长（cm）",
  `yb_ky_ycbttxsw_dx_width`  varchar(6)   NULL  COMMENT "咽-口咽-右侧扁桃体新生物-大小-宽（cm）",
  `yb_hy_zclzwxsw_yw`  varchar(2)   NULL  COMMENT "咽-喉咽-左侧梨状窝新生物（0:无 1:有）",
  `yb_hy_zclzwxsw_xt`  varchar(2)   NULL  COMMENT "咽-喉咽-左侧梨状窝新生物-形态（1:菜花型 2:结节或包块型 3:溃疡浸润型 4:混合型）",
  `yb_hy_zclzwxsw_bj`  varchar(2)   NULL  COMMENT "咽-喉咽-左侧梨状窝新生物-边界（1:不清 1:清）",
  `yb_hy_zclzwxsw_bmgh`  varchar(2)   NULL  COMMENT "咽-喉咽-左侧梨状窝新生物-表面光滑（0:否 1:是）",
  `yb_hy_zclzwxsw_bmkp`  varchar(2)   NULL  COMMENT "咽-喉咽-左侧梨状窝新生物-表面溃破（0:无 1:有）",
  `yb_hy_zclzwxsw_dx_length`  varchar(6)   NULL  COMMENT "咽-喉咽-左侧梨状窝新生物-大小-长（cm）",
  `yb_hy_zclzwxsw_dx_width`  varchar(6)   NULL  COMMENT "咽-喉咽-左侧梨状窝新生物-大小-宽（cm）",
  `yb_hy_yclzwxsw_yw`  varchar(2)   NULL  COMMENT "咽-喉咽-右侧梨状窝新生物（0:无 1:有）",
  `yb_hy_yclzwxsw_xt`  varchar(2)   NULL  COMMENT "咽-喉咽-右侧梨状窝新生物-形态（1:菜花型 2:结节或包块型 3:溃疡浸润型 4:混合型）",
  `yb_hy_yclzwxsw_bj`  varchar(2)   NULL  COMMENT "咽-喉咽-右侧梨状窝新生物-边界（1:不清 1:清）",
  `yb_hy_yclzwxsw_bmgh`  varchar(2)   NULL  COMMENT "咽-喉咽-右侧梨状窝新生物-表面光滑（0:否 1:是）",
  `yb_hy_yclzwxsw_bmkp`  varchar(2)   NULL  COMMENT "咽-喉咽-右侧梨状窝新生物-表面溃破（0:无 1:有）",
  `yb_hy_yclzwxsw_dx_length`  varchar(6)   NULL  COMMENT "咽-喉咽-右侧梨状窝新生物-大小-长（cm）",
  `yb_hy_yclzwxsw_dx_width`  varchar(6)   NULL  COMMENT "咽-喉咽-右侧梨状窝新生物-大小-宽（cm）",
  `yb_hy_hyhbxsw_yw`  varchar(2)   NULL  COMMENT "咽-喉咽-喉咽后壁新生物（0:无 1:有）",
  `yb_hy_hyhbxsw_xt`  varchar(2)   NULL  COMMENT "咽-喉咽-喉咽后壁新生物-形态（1:菜花型 2:结节或包块型 3:溃疡浸润型 4:混合型）",
  `yb_hy_hyhbxsw_bj`  varchar(2)   NULL  COMMENT "咽-喉咽-喉咽后壁新生物-边界（1:不清 1:清）",
  `yb_hy_hyhbxsw_bmgh`  varchar(2)   NULL  COMMENT "咽-喉咽-喉咽后壁新生物-表面光滑（0:否 1:是）",
  `yb_hy_hyhbxsw_bmkp`  varchar(2)   NULL  COMMENT "咽-喉咽-喉咽后壁新生物-表面溃破（0:无 1:有）",
  `yb_hy_hyhbxsw_dx_length`  varchar(6)   NULL  COMMENT "咽-喉咽-喉咽后壁新生物-大小-长（cm）",
  `yb_hy_hyhbxsw_dx_width`  varchar(6)   NULL  COMMENT "咽-喉咽-喉咽后壁新生物-大小-宽（cm）",
  `yb_hy_hhqxsw_yw`  varchar(2)   NULL  COMMENT "咽-喉咽-环后区新生物（0:无 1:有）",
  `yb_hy_hhqxsw_xt`  varchar(2)   NULL  COMMENT "咽-喉咽-环后区新生物-形态（1:菜花型 2:结节或包块型 3:溃疡浸润型 4:混合型）",
  `yb_hy_hhqxsw_bj`  varchar(2)   NULL  COMMENT "咽-喉咽-环后区新生物-边界（1:不清 1:清）",
  `yb_hy_hhqxsw_bmgh`  varchar(2)   NULL  COMMENT "咽-喉咽-环后区新生物-表面光滑（0:否 1:是）",
  `yb_hy_hhqxsw_bmkp`  varchar(2)   NULL  COMMENT "咽-喉咽-环后区新生物-表面溃破（0:无 1:有）",
  `yb_hy_hhqxsw_dx_length`  varchar(6)   NULL  COMMENT "咽-喉咽-环后区新生物-大小-长（cm）",
  `yb_hy_hhqxsw_dx_width`  varchar(6)   NULL  COMMENT "咽-喉咽-环后区新生物-大小-宽（cm）",
  `hb_hy_sm`  varchar(2)   NULL  COMMENT "喉-会厌-舌面（1:光滑 2:粗糙3:溃疡 4:新生物 5:充血 6:充血水肿 7:囊肿）",
  `hb_hy_hm`  varchar(2)   NULL  COMMENT "喉-会厌-喉面（1:光滑 2:粗糙3:溃疡 4:新生物 5:充血 6:充血水肿）",
  `hb_sd_ycsd`  varchar(2)   NULL  COMMENT "喉-声带-右侧声带（1:息肉样突起2:全程充血水肿 3:白斑样物4:乳头状新生物 5:菜花样新生物 6:蕈样新生物 7:边缘光滑 8:表面粗糙9:充血 10:肥厚 11:肉芽样物）",
  `hb_sd_zcsd`  varchar(2)   NULL  COMMENT "喉-声带-左侧声带（1:息肉样突起2:全程充血水肿 3:白斑样物4:乳头状新生物 5:菜花样新生物 6:蕈样新生物 7:边缘光滑 8:表面粗糙9:充血 10:肥厚 11:肉芽样物）",
  `hb_sd_sdhd`  varchar(2)   NULL  COMMENT "喉-声带-声带活动（1:双侧声带活动好 2:双侧声带固定 3:左侧声带固定，右侧运动正常 4:右侧声带固定， 左侧运动正常 5:左侧声带活动受限，右侧运动正常6:右侧声带活动受限，左侧运动正常 7:双侧声带活动受限）",
  `hb_shd_zcshd`  varchar(2)   NULL  COMMENT "喉-室带-左侧室带（1:光滑2:粗糙3:溃疡4:充血5:肥厚物6:新生）",
  `hb_shd_ycshd`  varchar(2)   NULL  COMMENT "喉-室带-右侧室带（1:光滑2:粗糙3:溃疡4:充血5:肥厚物6:新生）",
  `hb_pl_zcpl`  varchar(2)   NULL  COMMENT "喉-披裂-左侧披裂（1:光滑、活动好 2:可见新生物 3:固定）",
  `hb_pl_ycpl`  varchar(2)   NULL  COMMENT "喉-披裂-右侧披裂（1:光滑、活动好 2:可见新生物 3:固定）",
  `hb_sm`  varchar(2)   NULL  COMMENT "喉-声门（1:如常 2:声门裂1-2mm 3:声门裂2-3mm  4:声门裂3-4mm5:其他）",
  `eb_ek_jx`  varchar(2)   NULL  COMMENT "耳-耳廓-畸形（0:无 1:有）",
  `eb_ek_zcjx`  varchar(2)   NULL  COMMENT "耳-耳廓-左侧畸形（  0:无 1:小耳  2:挛缩3:猿耳  4:局耳 5:隐  耳 6:附耳 7:  移位耳 8:招  风耳）",
  `eb_ek_zcjxcd`  varchar(2)   NULL  COMMENT "耳-耳廓-左侧畸形程度（1:I ° 2:II °3:III°）",
  `eb_ek_ycjx`  varchar(2)   NULL  COMMENT "耳-耳廓-右侧畸形（0:无 1:小耳2:挛缩3:猿耳4:局耳 5:隐耳6:附耳 7:移位耳 8:招风耳）",
  `eb_ek_ycjxcd`  varchar(2)   NULL  COMMENT "耳-耳廓-右侧畸形程度（1:I ° 2:II °3:III°）",
  `eb_wed_zcwed`  varchar(2)   NULL  COMMENT "耳-外耳道-左外耳道（1:干洁 2:耵聍3:粘稠脓液 4:耵聍及粘稠脓液）",
  `eb_wed_ycwed`  varchar(2)   NULL  COMMENT "耳-外耳道-右外耳道（1:干洁 2:耵聍3:粘稠脓液 4:耵聍及粘稠脓液）",
  `eb_gm_zcgm`  varchar(2)   NULL  COMMENT "耳-鼓膜-左鼓膜（1:松弛部穿孔2:紧张部穿孔3:松弛部内陷袋 4:边缘性穿孔 5:完整）",
  `eb_gm_ycgm`  varchar(2)   NULL  COMMENT "耳-鼓膜-右鼓膜（1:松弛部穿孔2:紧张部穿孔3:松弛部内陷袋 4:边缘性穿孔 5:完整）",
  `eb_gs_zcgs`  varchar(2)   NULL  COMMENT "耳-鼓室-左鼓室（1:无积液 2:干燥 3:脓性分泌物 4:肉芽 5:胆脂瘤上皮 6:未窥及）",
  `eb_gs_ycgs`  varchar(2)   NULL  COMMENT "耳-鼓室-右鼓室（1:无积液 2:干燥 3:脓性分泌物 4:肉芽 5:胆脂瘤上皮 6:未窥及）",
  `eb_rt`  varchar(2)   NULL  COMMENT "耳-乳突（0:无红肿 1:有红肿）",
  `qt`  varchar(100)   NULL  COMMENT "其他",
  `zhpg_ecogpf`  varchar(2)   NULL  COMMENT "综合评估-ECOG评分（0:0 1:1 2:23:3 4:4 5:5）",
  `zhpg_kpspf`  varchar(2)   NULL  COMMENT "综合评估-Karnofsky评分(KPS)（0:0 1:10 2:203:30 4:405:50 6:607:70 8:809:90 10:100）",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_入院记录-专科检查';
-- 喉癌_入院记录-既往史
DROP TABLE IF EXISTS coc_zy_hbzl_ryjl_jws;
CREATE TABLE `coc_zy_hbzl_ryjl_jws` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `crbs_gys_yw`  varchar(2)   NULL  COMMENT "既往史-传染病史-肝炎史-有无（0:无 1:有）",
  `crbs_gys_gylx`  varchar(2)   NULL  COMMENT "既往史-传染病史-肝炎史-肝炎类型（1:甲肝2:乙肝大三阳3:乙肝小三阳4:丙肝5:其它）",
  `crbs_jhs_yw`  varchar(2)   NULL  COMMENT "既往史-传染病史-结核史-有无（0:无 1:有）",
  `crbs_jhs_bssc`  varchar(2)   NULL  COMMENT "既往史-传染病史-结核史-病史时长（年）",
  `crbs_njbs_yw`  varchar(2)   NULL  COMMENT "既往史-传染病史-疟疾病史-有无（0:无 1:有）",
  `crbs_njbs_bssc`  varchar(2)   NULL  COMMENT "既往史-传染病史-疟疾病史-病史时长（年）",
  `sswss_sss_yw`  varchar(2)   NULL  COMMENT "既往史-手术外伤史-手术史-有无（0:无 1:有）",
  `sswss_sss_sssj`  varchar(10)   NULL  COMMENT "既往史-手术外伤史-手术史-手术时间（年前）",
  `sswss_sss_ssmc`  varchar(100)   NULL  COMMENT "既往史-手术外伤史-手术史-手术名称",
  `sswss_wss_yw`  varchar(2)   NULL  COMMENT "既往史-手术外伤史-外伤史-有无（0:无 1:有）",
  `sswss_wss_wssj`  varchar(10)   NULL  COMMENT "既往史-手术外伤史-外伤史-外伤时间（年前）",
  `sswss_wss_wsms`  varchar(100)   NULL  COMMENT "既往史-手术外伤史-外伤史-外伤描述",
  `sswss_sxs_yw`  varchar(2)   NULL  COMMENT "既往史-手术外伤史-输血史-有无（0:无 1:有）",
  `sswss_sxs_sxsj`  varchar(10)   NULL  COMMENT "既往史-手术外伤史-输血史-输血时间（年）",
  `sswss_sxs_sxyy`  varchar(100)   NULL  COMMENT "既往史-手术外伤史-输血史-输血原因",
  `sswss_sxs_sxxx`  varchar(2)   NULL  COMMENT "既往史-手术外伤史-输血史-输血血型（1:O  1:A  2:B3:AB）",
  `sswss_sxs_sxl`  varchar(4)   NULL  COMMENT "既往史-手术外伤史-输血史-输血量（ml）",
  `gms_ywswgms`  varchar(2)   NULL  COMMENT "既往史-过敏史-药物食物过敏史（0:无 1:有）",
  `gms_ywswgmy`  varchar(200)   NULL  COMMENT "既往史-过敏史-药物食物过敏源（【多选】 1:过敏源不详、2:青霉素、3:磺胺类、4:头孢类、 5:解热镇痛药、6:安眠镇静药、7:抗通风药别嘌醇、 8:普鲁卡因、 9:鲑鱼降钙素、10:碘伏、 11:头孢曲松、 12:磷霉素、 13:链霉素、 14:酒精、15:花粉、16:螨虫）",
  `kjywsys`  varchar(20)   NULL  COMMENT "既往史-抗菌药物使用史（0:无 1:有）",
  `kjywsys_ywmc`  varchar(200)   NULL  COMMENT "既往史-抗菌药物使用史-药物名称",
  `yfjzs`  varchar(2)   NULL  COMMENT "既往史-预防接种史（1:随社会 2:不详 3:曾接种）",
  `yfjzs_jzymmc`  varchar(200)   NULL  COMMENT "既往史-预防接种史-接种疫苗名称（【多选】 1:麻疹活疫苗、2:乙型肝炎疫苗、 3:甲型肝炎疫苗、4:流行性乙型脑炎疫苗、5:脊髓灰质炎三型混合疫苗、6:流行性脊髓膜炎疫苗、7:卡介苗、 8:百白破菌苗）",
  `xthg_hxxt_mxkss_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-呼吸系统-慢性咳嗽史（0:无 1:有）",
  `xthg_hxxt_mxkss_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-呼吸系统-慢性咳嗽史-时长（年）",
  `xthg_hxxt_xts_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-呼吸系统-胸痛史（0:无 1:有）",
  `xthg_hxxt_xts_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-呼吸系统-胸痛史-时长（年）",
  `xthg_hxxt_kxs_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-呼吸系统-咯血史（0:无 1:有）",
  `xthg_hxxt_kxs_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-呼吸系统-咯血史-时长（年）",
  `xthg_hxxt_qcbs_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-呼吸系统-气喘病史（0:无 1:有）",
  `xthg_hxxt_qcbs_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-呼吸系统-气喘病史-时长（年）",
  `xthg_xhxt_xms_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-循环系统-胸闷史-有无（0:无 1:有）",
  `xthg_xhxt_xms_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-循环系统-胸闷史-时长（年）",
  `xthg_xhxt_xjs_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-循环系统-心悸史-有无（0:无 1:有）",
  `xthg_xhxt_xjs_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-循环系统-心悸史-时长（年）",
  `xthg_xhxt_xjts_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-循环系统-心绞痛史-有无（0:无 1:有）",
  `xthg_xhxt_xjts_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-循环系统-心绞痛史-时长（年）",
  `xthg_xhxt_xjgss_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-循环系统-心肌梗塞史-有无（0:无 1:有）",
  `xthg_xhxt_xjgss_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-循环系统-心肌梗塞史-时长（年）",
  `xthg_xhxt_gxys`  varchar(2)   NULL  COMMENT "既往史-系统回顾-循环系统-高血压史（0:无 1:有）",
  `xthg_xhxt_gxyxzbpxdbsywkz`  varchar(2)   NULL  COMMENT "既往史-系统回顾-循环系统-高血压、心脏病、贫血等病史药物控制（0:无 1:有）",
  `xthg_xhxt_xy_ssy`  varchar(3)   NULL  COMMENT "既往史-系统回顾-循环系统-血压-收缩压",
  `xthg_xhxt_xy_szy`  varchar(3)   NULL  COMMENT "既往史-系统回顾-循环系统-血压-舒张压",
  `xthg_xhuaxt_fts_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-消化系统-腹痛史-有无（0:无 1:有）",
  `xthg_xhuaxt_fts_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-消化系统-腹痛史-时长（年）",
  `xthg_xhuaxt_fxs_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-消化系统-腹泻史-有无（0:无 1:有）",
  `xthg_xhuaxt_fxs_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-消化系统-腹泻史-时长（年）",
  `xthg_xhuaxt_bxs_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-消化系统-便血史-有无（0:无 1:有）",
  `xthg_xhuaxt_bxs_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-消化系统-便血史-时长（年）",
  `xthg_xhuaxt_hds_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-消化系统-黄疸史-有无（0:无 1:有）",
  `xthg_xhuaxt_hds_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-消化系统-黄疸史-时长（年）",
  `xthg_mnxt_nps_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-泌尿系统-尿频史-有无（0:无 1:有）",
  `xthg_mnxt_nps_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-泌尿系统-尿频史-时长（年）",
  `xthg_mnxt_njs_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-泌尿系统-尿急史-有无（0:无 1:有）",
  `xthg_mnxt_njs_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-泌尿系统-尿急史-时长（年）",
  `xthg_mnxt_nts_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-泌尿系统-尿痛史-有无（0:无 1:有）",
  `xthg_mnxt_nts_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-泌尿系统-尿痛史-时长（年）",
  `xthg_mnxt_pnkns_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-泌尿系统-排尿困难史-有无（0:无 1:有）",
  `xthg_mnxt_pnkns_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-泌尿系统-排尿困难史-时长（年）",
  `xthg_xyxt_pxyxs_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-血液系统-皮下淤血史-有无（0:无 1:有）",
  `xthg_xyxt_pxyxs_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-血液系统-皮下淤血史-时长（年）",
  `xthg_xyxt_yycxs_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-血液系统-牙龈出血史-有无（0:无 1:有）",
  `xthg_xyxt_yycxs_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-血液系统-牙龈出血史-时长（年）",
  `xthg_xyxt_bnbs_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-血液系统-鼻衄病史-有无（0:无 1:有）",
  `xthg_xyxt_bnbs_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-血液系统-鼻衄病史-时长（年）",
  `xthg_nfmxt_dydsdns_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-内分泌系统-多饮多食多尿史-有无（0:无 1:有）",
  `xthg_nfmxt_tnbs_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-内分泌系统-糖尿病史-有无（0:无 1:有）",
  `xthg_nfmxt_tnbs_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-内分泌系统-糖尿病史-时长（年）",
  `xthg_nfmxt_tnbs_prxt`  varchar(4)   NULL  COMMENT "既往史-系统回顾-内分泌系统-糖尿病史-平日血糖（mmol/L）",
  `xthg_nfmxt_tnbs_zgxt`  varchar(4)   NULL  COMMENT "既往史-系统回顾-内分泌系统-糖尿病史-最高血糖（mmol/L）",
  `xthg_nfmxt_tnbs_fyywmc`  varchar(200)   NULL  COMMENT "既往史-系统回顾-内分泌系统-糖尿病史-服用药物名称",
  `xthg_nfmxt_tnbs_xtkzxg`  varchar(2)   NULL  COMMENT "既往史-系统回顾-内分泌系统-糖尿病史-血糖控制效果（0:不满意 1:满意）",
  `xthg_sjjsxt_tts_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-神经精神系统-头痛史-有无（0:无 1:有）",
  `xthg_sjjsxt_tts_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-神经精神系统-头痛史-时长（年）",
  `xthg_sjjsxt_sms_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-神经精神系统-失眠史-有无（0:无 1:有）",
  `xthg_sjjsxt_sms_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-神经精神系统-失眠史-时长（年）",
  `xthg_sjjsxt_hjs_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-神经精神系统-昏厥史-有无（0:无 1:有）",
  `xthg_sjjsxt_hjs_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-神经精神系统-昏厥史-时长（年）",
  `xthg_sjjsxt_ccs_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-神经精神系统-抽搐史-有无（0:无 1:有）",
  `xthg_sjjsxt_ccs_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-神经精神系统-抽搐史-时长（年）",
  `xthg_ydggxt_gjzts_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-运动骨骼系统-关节肿痛史-有无（0:无 1:有）",
  `xthg_ydggxt_gjzts_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-运动骨骼系统-关节肿痛史-时长（年）",
  `xthg_ydggxt_ydzas_yw`  varchar(2)   NULL  COMMENT "既往史-系统回顾-运动骨骼系统-运动障碍史-有无（0:无 1:有）",
  `xthg_ydggxt_ydzas_sc`  varchar(2)   NULL  COMMENT "既往史-系统回顾-运动骨骼系统-运动障碍史-时长（年）",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_入院记录-既往史';
-- 喉癌_入院记录（放疗）-系统回顾
DROP TABLE IF EXISTS coc_zy_hbzl_ryjlfl_xthg;
CREATE TABLE `coc_zy_hbzl_ryjlfl_xthg` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `hxxt_mxksbs`  varchar(2)   NULL  COMMENT "系统回顾-呼吸系统-慢性咳嗽病史（0:无 1:有）",
  `hxxt_mxksbssc`  varchar(10)   NULL  COMMENT "系统回顾-呼吸系统-慢性咳嗽-病史时长",
  `hxxt_xtbs`  varchar(2)   NULL  COMMENT "系统回顾-呼吸系统-胸痛病史（0:无 1:有）",
  `hxxt_xtbssc`  varchar(10)   NULL  COMMENT "系统回顾-呼吸系统-胸痛-病史时长",
  `hxxt_gxbs`  varchar(2)   NULL  COMMENT "系统回顾-呼吸系统-咯血病史（0:无 1:有）",
  `hxxt_gxbssc`  varchar(10)   NULL  COMMENT "系统回顾-呼吸系统-咯血-病史时长",
  `hxxt_qcbs`  varchar(2)   NULL  COMMENT "系统回顾-呼吸系统-气喘病史（0:无 1:有）",
  `hxxt_qcbssc`  varchar(10)   NULL  COMMENT "系统回顾-呼吸系统-气喘病史-时长",
  `xhxt_gxys`  varchar(2)   NULL  COMMENT "系统回顾-循环系统-高血压史（0:无 1:有）",
  `xhxt_gxys_sc`  varchar(10)   NULL  COMMENT "系统回顾-循环系统-高血压史-时长",
  `xhxt_gxys_xyzgz`  varchar(3)   NULL  COMMENT "系统回顾-循环系统-高血压史-血压最高值（mmHg）",
  `xhxt_gxys_mqfyywmc`  varchar(100)   NULL  COMMENT "系统回顾-循环系统-高血压史-目前服用药物名称",
  `xhxt_gxys_yyfs`  varchar(100)   NULL  COMMENT "系统回顾-循环系统-高血压史-用药方式",
  `xhxt_gxys_xykzz`  varchar(3)   NULL  COMMENT "系统回顾-循环系统-高血压史-血压控制值（mmHg）",
  `xhxt_gxbs`  varchar(2)   NULL  COMMENT "系统回顾-循环系统-冠心病史（0:无 1:有）",
  `xhxt_gxbs_sc`  varchar(20)   NULL  COMMENT "系统回顾-循环系统-冠心病史-时长",
  `xhxt_gxbs_zlfs`  varchar(200)   NULL  COMMENT "系统回顾-循环系统-冠心病史-治疗方式",
  `xhxt_gxbs_mqqk`  varchar(2)   NULL  COMMENT "系统回顾-循环系统-冠心病史-目前情况（0:不稳定 1:稳定）",
  `xhuaxt_ftbs`  varchar(2)   NULL  COMMENT "系统回顾-消化系统-腹痛病史（0:无 1:有）",
  `xhuaxt_ftbs_sc`  varchar(20)   NULL  COMMENT "系统回顾-消化系统-腹痛病史-时长",
  `xhuaxt_ftbs_fyyw`  varchar(200)   NULL  COMMENT "系统回顾-消化系统-腹痛病史-服用药物",
  `xhuaxt_ftbs_yyfs`  varchar(100)   NULL  COMMENT "系统回顾-消化系统-腹痛病史-用药方式",
  `xhuaxt_ftbs_mqqk`  varchar(2)   NULL  COMMENT "系统回顾-消化系统-腹痛病史-目前情况（0:不稳定 1:稳定）",
  `xhuaxt_fxbs`  varchar(2)   NULL  COMMENT "系统回顾-消化系统-腹泻病史（0:无 1:有）",
  `xhuaxt_fxbs_sc`  varchar(20)   NULL  COMMENT "系统回顾-消化系统-腹泻病史-时长",
  `xhuaxt_fxbs_fyyw`  varchar(200)   NULL  COMMENT "系统回顾-消化系统-腹泻病史-服用药物",
  `xhuaxt_fxbs_yyfs`  varchar(100)   NULL  COMMENT "系统回顾-消化系统-腹泻病史-用药方式",
  `xhuaxt_fxbs_mqqk`  varchar(2)   NULL  COMMENT "系统回顾-消化系统-腹泻病史-目前情况（0:不稳定 1:稳定）",
  `xhuaxt_bxbs`  varchar(2)   NULL  COMMENT "系统回顾-消化系统-便血病史（0:无 1:有）",
  `xhuaxt_bxbs_sc`  varchar(20)   NULL  COMMENT "系统回顾-消化系统-便血病史-时长",
  `xhuaxt_bxbs_fyyw`  varchar(200)   NULL  COMMENT "系统回顾-消化系统-便血病史-服用药物",
  `xhuaxt_bxbs_yyfs`  varchar(100)   NULL  COMMENT "系统回顾-消化系统-便血病史-用药方式",
  `xhuaxt_bxbs_mqqk`  varchar(2)   NULL  COMMENT "系统回顾-消化系统-便血病史-目前情况（0:不稳定 1:稳定）",
  `xhuaxt_hdbs`  varchar(2)   NULL  COMMENT "系统回顾-消化系统-黄疸病史（0:无 1:有）",
  `xhuaxt_hdbs_sc`  varchar(20)   NULL  COMMENT "系统回顾-消化系统-黄疸病史-时长",
  `xhuaxt_hdbs_fyyw`  varchar(200)   NULL  COMMENT "系统回顾-消化系统-黄疸病史-服用药物",
  `xhuaxt_hdbs_yyfs`  varchar(100)   NULL  COMMENT "系统回顾-消化系统-黄疸病史-用药方式",
  `xhuaxt_hdbs_mqqk`  varchar(2)   NULL  COMMENT "系统回顾-消化系统-黄疸病史-目前情况（0:不稳定 1:稳定）",
  `mnxt_np`  varchar(2)   NULL  COMMENT "系统回顾-泌尿系统-尿频（0:无 1:有）",
  `mnxt_np_sc`  varchar(20)   NULL  COMMENT "系统回顾-泌尿系统-尿频-时长",
  `mnxt_np_fyyw`  varchar(200)   NULL  COMMENT "系统回顾-泌尿系统-尿频-服用药物",
  `mnxt_np_yyfs`  varchar(100)   NULL  COMMENT "系统回顾-泌尿系统-尿频-用药方式",
  `mnxt_np_mqqk`  varchar(2)   NULL  COMMENT "系统回顾-泌尿系统-尿频-目前情况（0:不稳定 1:稳定）",
  `mnxt_nj`  varchar(2)   NULL  COMMENT "系统回顾-泌尿系统-尿急（0:无 1:有）",
  `mnxt_nj_sc`  varchar(20)   NULL  COMMENT "系统回顾-泌尿系统-尿急-时长",
  `mnxt_nj_fyyw`  varchar(200)   NULL  COMMENT "系统回顾-泌尿系统-尿急-服用药物",
  `mnxt_nj_yyfs`  varchar(100)   NULL  COMMENT "系统回顾-泌尿系统-尿频-用药方式",
  `mnxt_nj_mqqk`  varchar(2)   NULL  COMMENT "系统回顾-泌尿系统-尿急-目前情况（0:不稳定 1:稳定）",
  `mnxt_nt`  varchar(2)   NULL  COMMENT "系统回顾-泌尿系统-尿痛（0:无 1:有）",
  `mnxt_nt_sc`  varchar(20)   NULL  COMMENT "系统回顾-泌尿系统-尿痛-时长",
  `mnxt_nt_fyyw`  varchar(200)   NULL  COMMENT "系统回顾-泌尿系统-尿痛-服用药物",
  `mnxt_nt_yyfs`  varchar(100)   NULL  COMMENT "系统回顾-泌尿系统-尿痛-用药方式",
  `mnxt_nt_mqqk`  varchar(2)   NULL  COMMENT "系统回顾-泌尿系统-尿痛-目前情况（0:不稳定 1:稳定）",
  `mnxt_pnkn`  varchar(2)   NULL  COMMENT "系统回顾-泌尿系统-排尿困难（0:无 1:有）",
  `mnxt_pnkn_sc`  varchar(20)   NULL  COMMENT "系统回顾-泌尿系统-排尿困难-时长",
  `mnxt_pnkn_fyyw`  varchar(200)   NULL  COMMENT "系统回顾-泌尿系统-排尿困难-服用药物",
  `mnxt_pnkn_yyfs`  varchar(100)   NULL  COMMENT "系统回顾-泌尿系统-排尿困难-用药方式",
  `mnxt_pnkn_mqqk`  varchar(2)   NULL  COMMENT "系统回顾-泌尿系统-排尿困难-目前情况（0:不稳定 1:稳定）",
  `xyxt_bns`  varchar(2)   NULL  COMMENT "系统回顾-血液系统-鼻衄史（0:无 1:有）",
  `xyxt_bns_sc`  varchar(20)   NULL  COMMENT "系统回顾-血液系统-鼻衄史-时长",
  `xyxt_bns_zlfs`  varchar(200)   NULL  COMMENT "系统回顾-血液系统-鼻衄史-治疗方式",
  `xyxt_bns_mqqk`  varchar(2)   NULL  COMMENT "系统回顾-血液系统-鼻衄史-目前清理（0:不稳定 1:稳定）",
  `xyxt_pxyxs`  varchar(2)   NULL  COMMENT "系统回顾-血液系统-皮下淤血史（0:无 1:有）",
  `xyxt_pxyxs_sc`  varchar(20)   NULL  COMMENT "系统回顾-血液系统-皮下淤血史-时长",
  `xyxt_pxyxs_zlfs`  varchar(200)   NULL  COMMENT "系统回顾-血液系统-皮下淤血史-治疗方式",
  `xyxt_pxyxs_mqqk`  varchar(2)   NULL  COMMENT "系统回顾-血液系统-皮下淤血史-目前清理（0:不稳定 1:稳定）",
  `xyxt_yycxs`  varchar(2)   NULL  COMMENT "系统回顾-血液系统-牙龈出血史（0:无 1:有）",
  `xyxt_yycxs_sc`  varchar(20)   NULL  COMMENT "系统回顾-血液系统-牙龈出血史-时长",
  `xyxt_yycxs_zlfs`  varchar(200)   NULL  COMMENT "系统回顾-血液系统-牙龈出血史-治疗方式",
  `xyxt_yycxs_mqqk`  varchar(2)   NULL  COMMENT "系统回顾-血液系统-牙龈出血史-目前清理（0:不稳定 1:稳定）",
  `nfmxt_tnbs`  varchar(2)   NULL  COMMENT "系统回顾-内分泌系统-糖尿病史（0:无 1:有）",
  `nfmxt_tnbs_sc`  varchar(210)   NULL  COMMENT "系统回顾-内分泌系统-糖尿病史-时长",
  `nfmxt_tnbs_fyypmcjyyfs`  varchar(200)   NULL  COMMENT "系统回顾-内分泌系统-糖尿病史-服用药品名称及用药方式",
  `nfmxt_tnbs_xtkzz`  varchar(2)   NULL  COMMENT "系统回顾-内分泌系统-糖尿病史-血糖控制值（mmol/L）",
  `sjjsxt_dx`  varchar(2)   NULL  COMMENT "系统回顾-神经精神系统-癫痫（0:无 1:有）",
  `sjjsxt_dx_sc`  varchar(20)   NULL  COMMENT "系统回顾-神经精神系统-癫痫-时长",
  `sjjsxt_dx_fyyw`  varchar(200)   NULL  COMMENT "系统回顾-神经精神系统-癫痫-服用药物",
  `sjjsxt_dx_mqqk`  varchar(2)   NULL  COMMENT "系统回顾-神经精神系统-癫痫-目前情况（0:不稳定 1:稳定）",
  `sjjsxt_jj`  varchar(2)   NULL  COMMENT "系统回顾-神经精神系统-惊厥（0:无 1:有）",
  `sjjsxt_jj_sc`  varchar(20)   NULL  COMMENT "系统回顾-神经精神系统-惊厥-时长",
  `sjjsxt_jj_fyyw`  varchar(200)   NULL  COMMENT "系统回顾-神经精神系统-惊厥-服用药物",
  `sjjsxt_jj_mqqk`  varchar(2)   NULL  COMMENT "系统回顾-神经精神系统-惊厥-目前情况（0:不稳定 1:稳定）",
  `sjjsxt_zk`  varchar(2)   NULL  COMMENT "系统回顾-神经精神系统-躁狂（0:无 1:有）",
  `sjjsxt_zk_sc`  varchar(20)   NULL  COMMENT "系统回顾-神经精神系统-躁狂-时长",
  `sjjsxt_zk_fyyw`  varchar(200)   NULL  COMMENT "系统回顾-神经精神系统-躁狂-服用药物",
  `sjjsxt_zk_mqqk`  varchar(2)   NULL  COMMENT "系统回顾-神经精神系统-躁狂-目前情况（0:不稳定 1:稳定）",
  `sjjsxt_yybs`  varchar(2)   NULL  COMMENT "系统回顾-神经精神系统-抑郁病史（0:无 1:有）",
  `sjjsxt_yybs_sc`  varchar(20)   NULL  COMMENT "系统回顾-神经精神系统-抑郁病史-时长",
  `sjjsxt_yybs_fyyw`  varchar(200)   NULL  COMMENT "系统回顾-神经精神系统-抑郁病史-服用药物",
  `sjjsxt_yybs_mqqk`  varchar(2)   NULL  COMMENT "系统回顾-神经精神系统-抑郁病史-目前情况（0:不稳定 1:稳定）",
  `ydggxt_gjzt`  varchar(2)   NULL  COMMENT "系统回顾-运动骨骼系统-关节肿痛（0:无 1:有）",
  `ydggxt_gjzt_sc`  varchar(20)   NULL  COMMENT "系统回顾-运动骨骼系统-关节肿痛-时长",
  `ydggxt_gjzt_zlfs`  varchar(200)   NULL  COMMENT "系统回顾-运动骨骼系统-关节肿痛-治疗方式",
  `ydggxt_gjzt_mqqk`  varchar(2)   NULL  COMMENT "系统回顾-运动骨骼系统-关节肿痛-目前情况（0:不稳定 1:稳定）",
  `ydggxt_ydza`  varchar(2)   NULL  COMMENT "系统回顾-运动骨骼系统-运动障碍",
  `ydggxt_ydza_sc`  varchar(20)   NULL  COMMENT "系统回顾-运动骨骼系统-运动障碍-时长",
  `ydggxt_ydza_zlfs`  varchar(200)   NULL  COMMENT "系统回顾-运动骨骼系统-运动障碍-治疗方式",
  `ydggxt_ydza_mqqk`  varchar(2)   NULL  COMMENT "系统回顾-运动骨骼系统-运动障碍-目前情况（0:不稳定 1:稳定）",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_入院记录（放疗）-系统回顾';
-- 喉癌_入院记录-体格检查
DROP TABLE IF EXISTS coc_zy_hbzl_ryjl_tgjc;
CREATE TABLE `coc_zy_hbzl_ryjl_tgjc` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `tw`  varchar(6)   NULL  COMMENT "体温（℃）",
  `ml`  varchar(4)   NULL  COMMENT "脉率（次/分）",
  `hx`  varchar(4)   NULL  COMMENT "呼吸（次/分）",
  `ssx`  varchar(4)   NULL  COMMENT "收缩压（mmHg）",
  `szy`  varchar(4)   NULL  COMMENT "舒张压（mmHg）",
  `sybqk_fy`  varchar(2)   NULL  COMMENT "一般情况-发育（1:正常 2:不良3:超常 4:异常）",
  `sybqk_yy`  varchar(2)   NULL  COMMENT "一般情况-营养（1: 良好 2:中等3:不良 4:恶病质）",
  `sybqk_mr`  varchar(2)   NULL  COMMENT "一般情况-面容（1:无病容 2:急3:慢性病容）",
  `sybqk_bq`  varchar(2)   NULL  COMMENT "一般情况-表情（1: 自如 2:痛苦3:忧虑 4:恐惧5:淡漠）",
  `sybqk_sz`  varchar(2)   NULL  COMMENT "一般情况-神志（1:清醒 2:嗜睡3:模糊 4:昏睡5:昏迷 6:谵妄）",
  `sybqk_rbffs`  varchar(2)   NULL  COMMENT "一般情况-入病房方式（1:步入病房 2:抱入病房 3:抬入病房 4:推入病房）",
  `sybqk_cthz`  varchar(2)   NULL  COMMENT "一般情况-查体合作（0:不合作 1:合作2:欠合作）",
  `pfnm_sz`  varchar(2)   NULL  COMMENT "皮肤黏膜-色泽（1:正常2:潮红3:苍白4:发绀5:黄染6:色素7:沉重）",
  `pfnm_pz`  varchar(2)   NULL  COMMENT "皮肤黏膜-皮疹（0:无 1:有）",
  `pfnm_pxcx`  varchar(2)   NULL  COMMENT "皮肤黏膜-皮下出血（0:无 1:有）",
  `pfnm_shz`  varchar(2)   NULL  COMMENT "皮肤黏膜-水肿（0:无 1:有）",
  `pfnm_gz`  varchar(2)   NULL  COMMENT "皮肤黏膜-肝掌（0:无 1:有）",
  `pfnm_zzz`  varchar(2)   NULL  COMMENT "皮肤黏膜-蜘蛛痣（0:无 1:有）",
  `tmb_ms`  varchar(200)   NULL  COMMENT "头面部-描述",
  `tmb_yc`  varchar(2)   NULL  COMMENT "头面部-牙齿（1:整齐 2：缺齿）",
  `jbzczk_yw`  varchar(2)   NULL  COMMENT "颈部-左侧肿块-有无（1:有 0:无）",
  `jbzczk_zkwz`  varchar(2)   NULL  COMMENT "颈部-左侧肿块-肿块位置（1:颏下三角 2:下颌下三角 3:颈动脉三角 4:肌三角5:枕三角 6:锁骨上三角 7:胸骨上区8:其他）",
  `jbzczk_zkzd`  varchar(2)   NULL  COMMENT "颈部-左侧肿块-肿块质地（1:硬 2:韧 3:软）",
  `jbzczk_zkbj`  varchar(2)   NULL  COMMENT "颈部-左侧肿块-肿块边界（1:清  0:不清）",
  `jbzczk_bmgh`  varchar(2)   NULL  COMMENT "颈部-左侧肿块-表面光滑（1.是  2.否）",
  `jbzczk_zkhd`  varchar(2)   NULL  COMMENT "颈部-左侧肿块-活动（1:可 2:固定）",
  `jbzczk_zkyt`  varchar(2)   NULL  COMMENT "颈部-左侧肿块-压痛（1:有 0:无）",
  `jbzczk_pfpk`  varchar(2)   NULL  COMMENT "颈部-左侧肿块-皮肤溃破（1:有 0:无）",
  `jbzczk_zkdx_length`  varchar(4)   NULL  COMMENT "颈部-左侧肿块-肿块大小-长（cm）",
  `jbzczk_zkdx_width`  varchar(4)   NULL  COMMENT "颈部-左侧肿块-肿块大小-宽（cm）",
  `jbyczk_yw`  varchar(2)   NULL  COMMENT "颈部-右侧肿块-有无（1:有 0:无）",
  `jbyczk_zkwz`  varchar(2)   NULL  COMMENT "颈部-右侧肿块-肿块位置（1:颏下三角 2:下颌下三角 3:颈动脉三角 4:肌三角5:枕三角 6:锁骨上三角 7:胸骨上区8:其他）",
  `jbyczk_zkzd`  varchar(2)   NULL  COMMENT "颈部-右侧肿块-肿块质地（1:硬 2:韧 3:软）",
  `jbyczk_zkbj`  varchar(2)   NULL  COMMENT "颈部-右侧肿块-肿块边界（1:清 0:不清）",
  `jbyczk_bmgh`  varchar(2)   NULL  COMMENT "颈部-右侧肿块-表面光滑（1:是  0:否）",
  `jbyczk_zkhd`  varchar(2)   NULL  COMMENT "颈部-右侧肿块-活动（1:可 2:固定）",
  `jbyczk_zkyt`  varchar(2)   NULL  COMMENT "颈部-右颈侧肿块-压痛（1:有 0:无）",
  `jbyczk_pfpk`  varchar(2)   NULL  COMMENT "颈部-右侧肿块-皮肤溃破（1:有 0:无）",
  `jbyczk_zkdx_length`  varchar(4)   NULL  COMMENT "颈部-右侧肿块-肿块大小-长（cm）",
  `jbyczk_zkdx_width`  varchar(4)   NULL  COMMENT "颈部-右侧肿块-肿块大小-宽（cm）",
  `jbqg_qgwz`  varchar(2)   NULL  COMMENT "颈部-气管位置（1:居中 2:左偏3:右偏）",
  `jbqg_jbqgqk`  varchar(2)   NULL  COMMENT "颈部-颈部气管切开（1:有 0:无）",
  `jbqg_jbqgqk_gjqgt`  varchar(2)   NULL  COMMENT "颈部-颈部气管切开-硅胶气管筒（1:00号 2:0号3:1号 4:2号5:3号 6:4号7:5号 8:6号9:加长 10:其他）",
  `jzx_jzxbk`  varchar(2)   NULL  COMMENT "甲状腺-甲状腺包块（0:未触及明显包块 1:触及包块）",
  `jzx_zcbk_yw`  varchar(2)   NULL  COMMENT "甲状腺-左侧甲状腺包块-有无（0:无 1:有）",
  `jzx_zcbk_zd`  varchar(2)   NULL  COMMENT "甲状腺-左侧甲状腺包块-质地（1:硬 2:韧 3:软）",
  `jzx_zcbk_bj`  varchar(2)   NULL  COMMENT "甲状腺-左侧甲状腺包块-边界（0:不清 1:清）",
  `jzx_zcbk_bmgh`  varchar(2)   NULL  COMMENT "甲状腺-左侧甲状腺包块-表面光滑（0:否 1:是）",
  `jzx_zcbk_hd`  varchar(2)   NULL  COMMENT "甲状腺-左侧甲状腺包块-活动（1:可 2:固定）",
  `jzx_zcbk_yt`  varchar(2)   NULL  COMMENT "甲状腺-左侧甲状腺包块-压痛（0:无 1:有）",
  `jzx_zcbk_pfkp`  varchar(2)   NULL  COMMENT "甲状腺-左侧甲状腺包块-皮肤溃破（0:无 1:有）",
  `jzx_zcbk_dx_length`  varchar(6)   NULL  COMMENT "甲状腺-左侧甲状腺包块-大小-长（cm）",
  `jzx_zcbk_dx_width`  varchar(6)   NULL  COMMENT "甲状腺-左侧甲状腺包块-大小-宽（cm）",
  `jzx_ycbk_yw`  varchar(2)   NULL  COMMENT "甲状腺-右侧甲状腺包块-有无（0:无 1:有）",
  `jzx_ycbk_zd`  varchar(2)   NULL  COMMENT "甲状腺-右侧甲状腺包块-质地（1:硬 2:韧 3:软）",
  `jzx_ycbk_bj`  varchar(2)   NULL  COMMENT "甲状腺-右侧甲状腺包块-边界（0:不清 1:清）",
  `jzx_ycbk_bmgh`  varchar(2)   NULL  COMMENT "甲状腺-右侧甲状腺包块-表面光滑（0:否 1:是）",
  `jzx_ycbk_hd`  varchar(2)   NULL  COMMENT "甲状腺-右侧甲状腺包块-活动（1:可 2:固定）",
  `jzx_ycbk_yt`  varchar(2)   NULL  COMMENT "甲状腺-右侧甲状腺包块-压痛（0:无 1:有）",
  `jzx_ycbk_pfkp`  varchar(2)   NULL  COMMENT "甲状腺-右侧甲状腺包块-皮肤溃破（0:无 1:有）",
  `jzx_ycbk_dx_length`  varchar(6)   NULL  COMMENT "甲状腺-右侧甲状腺包块-大小-长（cm）",
  `jzx_ycbk_dx_width`  varchar(6)   NULL  COMMENT "甲状腺-右侧甲状腺包块-大小-宽（cm）",
  `jzx_jbbk_yw`  varchar(2)   NULL  COMMENT "甲状腺-峡部包块-有无（0:无 1:有）",
  `jzx_jbbk_zd`  varchar(2)   NULL  COMMENT "甲状腺-峡部包块-质地（1:硬 2:韧 3:软）",
  `jzx_jbbk_bj`  varchar(2)   NULL  COMMENT "甲状腺-峡部包块-边界（0:不清 1:清）",
  `jzx_jbbk_bmgh`  varchar(2)   NULL  COMMENT "甲状腺-峡部包块-表面光滑（0:否 1:是）",
  `jzx_jbbk_hd`  varchar(2)   NULL  COMMENT "甲状腺-峡部包块-活动（1:可 2:固定）",
  `jzx_jbbk_yt`  varchar(2)   NULL  COMMENT "甲状腺-峡部包块-压痛（0:无 1:有）",
  `jzx_jbbk_pfkp`  varchar(2)   NULL  COMMENT "甲状腺-峡部包块-皮肤溃破（0:无 1:有）",
  `jzx_jbbk_dx_length`  varchar(6)   NULL  COMMENT "甲状腺-峡部包块-大小-长（cm）",
  `jzx_jbbk_dx_width`  varchar(6)   NULL  COMMENT "甲状腺-峡部包块-大小-宽（cm）",
  `jzx_xgswax`  varchar(2)   NULL  COMMENT "甲状腺-胸骨上窝凹陷（0:无 1:有）",
  `jzx_sgswax`  varchar(2)   NULL  COMMENT "甲状腺-锁骨上窝凹陷（0:无 1:有）",
  `xb_xb_lc`  varchar(2)   NULL  COMMENT "胸部-胸壁-两侧（0:不对称 1:对称）",
  `xb_xb_jx`  varchar(2)   NULL  COMMENT "胸部-胸壁-畸形（0:无 1:有）",
  `xb_xb_ljxax`  varchar(2)   NULL  COMMENT "胸部-胸壁-肋间隙凹陷（0:无 1:有）",
  `xb_fhxy`  varchar(2)   NULL  COMMENT "胸部-肺呼吸音（1:清 2:粗）",
  `xb_gsly`  varchar(2)   NULL  COMMENT "胸部-干湿罗音（0:未闻及 1:可闻及）",
  `xb_xmy`  varchar(2)   NULL  COMMENT "胸部-哮鸣音（0:无 1:有）",
  `xb_xlcs`  varchar(6)   NULL  COMMENT "胸部-心率次数（次/分）",
  `xb_xljl`  varchar(2)   NULL  COMMENT "胸部-心率结论（1:齐 2:不齐3:绝对不齐）",
  `xb_fb_ms`  varchar(200)   NULL  COMMENT "腹部-腹壁-描述",
  `xb_fb_bh`  varchar(2)   NULL  COMMENT "腹部-腹壁-瘢痕（0:无 1:有）",
  `xb_gz`  varchar(2)   NULL  COMMENT "腹部-肝脏（0:肋下未及 1:肋下可及）",
  `xb_pz`  varchar(2)   NULL  COMMENT "腹部-脾脏（0:肋下未及 1:肋下可及）",
  `jzsz_jx`  varchar(2)   NULL  COMMENT "脊柱四肢-畸形（0:无 1:有）",
  `jzsz_gjhd`  varchar(2)   NULL  COMMENT "脊柱四肢-关节活动（自如/受限）",
  `gmwszq`  varchar(200)   NULL  COMMENT "肛门外生殖器",
  `sjxt_slfs`  varchar(2)   NULL  COMMENT "神经系统-生理反射（0:消失 1:存在）",
  `sjxt_blfs`  varchar(2)   NULL  COMMENT "神经系统-病理反射（0:未引出 1:引出）",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_入院记录-体格检查';
-- 喉癌_入院记录-现病史
DROP TABLE IF EXISTS coc_zy_hbzl_ryjl_xbs;
CREATE TABLE `coc_zy_hbzl_ryjl_xbs` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `fbrq`  varchar(20)   NULL  COMMENT "现病史-发病日期",
  `yy`  varchar(2)   NULL  COMMENT "现病史-诱因（1:无明显诱因2:感冒 3:过度发声）",
  `zz`  varchar(200)   NULL  COMMENT "现病史-症状",
  `fr`  varchar(2)   NULL  COMMENT "现病史-发热（1:伴 0:不伴）",
  `ybywg`  varchar(2)   NULL  COMMENT "现病史-咽部异物感（1:伴 0:不伴）",
  `yt`  varchar(2)   NULL  COMMENT "现病史-咽痛（1:伴 0:不伴）",
  `ks`  varchar(2)   NULL  COMMENT "现病史-咳嗽（1:伴 0:不伴）",
  `kt`  varchar(2)   NULL  COMMENT "现病史-咳痰（1:伴 0:不伴）",
  `kx`  varchar(2)   NULL  COMMENT "现病史-咳血（1:伴 0:不伴）",
  `hxbc`  varchar(2)   NULL  COMMENT "现病史-呼吸不畅（1:伴 0:不伴）",
  `xm`  varchar(2)   NULL  COMMENT "现病史-胸闷（1:伴 0:不伴）",
  `ysqk`  varchar(2)   NULL  COMMENT "现病史-饮水呛咳（1:伴 0:不伴）",
  `jszg`  varchar(2)   NULL  COMMENT "现病史-进食梗阻（1:伴 0:不伴）",
  `jbbk`  varchar(2)   NULL  COMMENT "现病史-颈部包块（1:伴 0:不伴）",
  `zlfs`  varchar(2)   NULL  COMMENT "现病史-治疗方式（0:未治疗 1:抗炎治疗 2:口服中成药物 3:禁声休息）",
  `zlxg`  varchar(2)   NULL  COMMENT "现病史-治疗效果（0:无效 1:稍缓解）",
  `ssjzsc`  varchar(10)   NULL  COMMENT "现病史-声嘶加重时长",
  `fzjcjg`  varchar(500)   NULL  COMMENT "现病史-辅助检查结果",
  `hjbljg`  varchar(500)   NULL  COMMENT "现病史-活检病理结果",
  `hzjg`  varchar(500)   NULL  COMMENT "现病史-会诊结果",
  `ryyy`  varchar(2)   NULL  COMMENT "现病史-入院原因（1:喉癌 2:喉新生物）",
  `ybqk`  varchar(2)   NULL  COMMENT "现病史-一般情况（1:好 2:可 3:差）",
  `yssm`  varchar(2)   NULL  COMMENT "现病史-饮食睡眠（1:佳 2:差）",
  `dxb`  varchar(2)   NULL  COMMENT "现病史-大小便（0:不正常 1:正常）",
  `tzmxxj`  varchar(2)   NULL  COMMENT "现病史-体重明显下降（1:有  0:无）",
PRIMARY KEY (`ID`)
) COMMENT = '喉癌_入院记录-现病史';
-- 喉癌_入院记录（放疗）
DROP TABLE IF EXISTS coc_zy_hbzl_ryjlfl;
CREATE TABLE `coc_zy_hbzl_ryjlfl` (
  `id` bigint(20) NOT NULL AUTO_INCREMENT COMMENT 'id',
  `yljgdm` varchar(11) NOT NULL COMMENT '医疗机构代码',
  `hzbh` varchar(32) NOT NULL COMMENT '患者编号，COC患者清单表外键；身份证号/其他证件类型+证件号码',
  `jzlsh` varchar(32) NOT NULL COMMENT '就诊流水号，用于与住院就诊记录表或门诊就诊记录表关联的外键',
  `jlsj` varchar(32) COMMENT '记录时间',
  `kh`  varchar(32)   NOT NULL  COMMENT "卡号（患者就诊卡卡号）",
  `klx`  varchar(16)   NOT NULL  COMMENT "卡类型（参见字典表）",
  `xgbz`  varchar(1)   NOT NULL  COMMENT "修改标志（1:正常 2:修改3:撤销）",
  `yjlxh`  varchar(32)   NOT NULL  COMMENT "原纪录序号（院内唯一标识）",
  `hzxm`  varchar(50)   NULL  COMMENT "患者姓名",
  `hzxb`  varchar(10)   NULL  COMMENT "患者性别",
  `hznl`  varchar(10)   NULL  COMMENT "患者年龄",
  `hzmz`  varchar(20)   NULL  COMMENT "患者民族",
  `hzjg`  varchar(100)   NULL  COMMENT "患者籍贯",
  `hzhy`  varchar(20)   NULL  COMMENT "患者婚姻",
  `hzzy`  varchar(50)   NULL  COMMENT "患者职业",
  `hzxjd`  varchar(100)   NULL  COMMENT "患者现居地",
  `gsz`  varchar(2)   NULL  COMMENT "供史者（1:患者本人 2:患者家属 3:其他）",
  `rysj`  varchar(20)   NULL  COMMENT "入院时间",
  `zs`  varchar(2000)   NULL  COMMENT "主诉",
  `hys_hyzk`  varchar(2)   NULL  COMMENT "婚育史-婚姻状况（1:已婚 2:未婚3:丧偶 4:离异）",
  `hys_syqk`  varchar(2)   NULL  COMMENT "婚育史-生育情况（0:未育 1:已育）",
  `hys_syezsl`  varchar(2)   NULL  COMMENT "婚育史-生育儿子数量",
  `hys_synesl`  varchar(2)   NULL  COMMENT "婚育史-生育女儿数量",
  `jzs_fmsczt`  varchar(2)   NULL  COMMENT "家族史-父母生存状态（1:父亲健在 2:母亲健在 3:父母健在 4:父亲已故5:母亲已故 6:父母已故）",
  `jzs_fmsgyy`  varchar(100)   NULL  COMMENT "家族史-父母身故原因",
  `jzs_xdjmsczt`  varchar(50)   NULL  COMMENT "家族史-兄弟姐妹生存状态",
  `jzs_xdjmsgyy`  varchar(100)   NULL  COMMENT "家族史-兄弟姐妹身故原因",
  `jzs_jzxycbs`  varchar(2)   NULL  COMMENT "家族史-家族性遗传病史（0:否 1:是）",
  `cbzd`  varchar(100)   NULL  COMMENT "初步诊断",
  `cbzd_halx`  varchar(2)   NULL  COMMENT "喉癌类型（1:声门上型 2:声门型 3:声门下型4:跨声门型）",
  `cbzdfq_t`  varchar(2)   NULL  COMMENT "诊断分期-T（1:X 2:0 3:1 4:25:3 6:4）",
  `cbzdfq_n`  varchar(2)   NULL  COMMENT "诊断分期-N（1:X 2:0 3:1 4:25:3）",
  `cbzdfq_m`  varchar(2)   NULL  COMMENT "诊断分期-M（1:0 2:1）",
  `cbzdfq_lcfq`  varchar(2)   NULL  COMMENT "临床分期（1:0 2:I 3:II4:III 5:IVA6:IVB 7:IVC）",
  `zzys`  varchar(50)   NULL  COMMENT "主治医师",
  `fzrys`  varchar(50)   NULL  COMMENT "副主任医师",
  `jlrq`  varchar(20)   NULL  COMMENT "记录日期",
  PRIMARY KEY (`ID`)
  ) COMMENT = '喉癌_入院记录（放疗）';
    """
    
    # 执行创建表的 SQL 语句
    cursor.execute(create_table_sql)
    # print("表 'coc_zy_hbzl_flxj' 创建成功")
    
    # 提交事务
    conn.commit()
    
    # # 插入示例数据
    # insert_data_sql = """
    # INSERT INTO coc_zy_hbzl_flxj (
    #     yljgdm, hzbh, jzlsh, jlsj, kh, klx, xgbz, yjlxh, zlkssj, zljssj, zd, ybqk_zyzzjtz_xm, ybqk_zyzzjtz_xb, ybqk_zyzzjtz_nl, ybqk_zyzzjtz_zsms, ybqk_zyzzjtz_ryzd, ybqk_zyzzjtz_ryrq, ybqk_sg, ybqk_tz, ybqk_kpspf, ybqk_xbs, zyfzjc_blbg, zyfzjc_hbctmri, zyfzjc_sysjc_bxb, zyfzjc_sysjc_hxb, zyfzjc_sysjc_xxb, zyfzjc_sysjc_gbzam, zyfzjc_sysjc_gczam, zyfzjc_sysjc_rstqm, zyfzjc_sysjc_jlz, zyfzjc_sysjc_nlz, zyfzjc_sysjc_llz, zljg_zlksrq, zljg_zljsrq, zljg_zlfs, zljg_jtfa, zljg_zlgc, zljg_blfydj, zljg_blfylx, zljg_zlzt, zljg_zllx, sfzdfl, zdfl_zdyy, zdfl_zdts, sftbhl, tbhl_ym, tbhl_jl, tbhl_ts, tbhl_yf, tbhl_pc, tbhl_lc, sftbbx, tbbx_ym, tbbx_jl, tbbx_yf, tbbx_pc, tbbx_cs, sftbmy, tbmy_ym, tbmy_jyl, tbmy_yf, tbmy_pc, tbmy_cs, fljshlxpg_yfz, fljshlxpg_jblbj, flbwbm, flbwmc, flbwcxbm, flbwcxmc, cyqk, cyzd_cydy, cyzd_kfzd, cyzd_sfjfz, cyzd_xjsjzqk, zzys, zrfzrys, xjsj
    # ) VALUES (
    #     '12345678901', 'A1234567890123456789', 'JZL001', '2023-10-01 10:00:00', 'KH001', 'VIP', '1', 'YJ001', '2023-10-01', '2023-10-30', '喉癌', '张三', '男', '50', '喉咙痛', '喉癌', '2023-10-01', '175', '70', '8', '无特殊', '病理报告内容', 'CT/MR结果', '5.0', '4.5', '300', '25', '30', '40', '50', '140', '100', '2023-10-01', '2023-10-30', '1', '具体方案', '1', '1', '1', '1', '1', '0', NULL, NULL, '1', '1', '100', '3', '1', '1', '1', '0', NULL, NULL, NULL, NULL, NULL, '0', NULL, NULL, NULL, NULL, NULL, '1', '0', 'BW001', '喉部', 'CX001', '左侧', '放疗完成情况良好', '出院带药说明', '康复指导内容', '随访及复诊安排', '需及时就诊的情况说明', '主治医师张三', '主任医师李四', '2023-10-30'
    # );
    # """
    
    # # 执行插入数据的 SQL 语句
    # cursor.execute(insert_data_sql)
    # print("示例数据插入成功")
    
    # # 提交事务
    # conn.commit()
    
   
    
    # 关闭数据库连接
    conn.close()
    print("\n数据库操作完成，连接已关闭")

except pymysql.Error as e:
    print(f"MySQL错误: {e}")
    
    # 如果是连接错误，提供一些建议
    if "Access denied" in str(e):
        print("\n可能的解决方案:")
        print("1. 检查MySQL用户名和密码是否正确")
        print("2. 确保MySQL服务器正在运行")
        print("3. 如果使用的是远程MySQL服务器，确保您的IP地址被允许连接")
        print("4. 尝试使用以下命令连接MySQL以验证凭据:")
        print("   mysql -u root -p")
        
    elif "Can't connect" in str(e):
        print("\n可能的解决方案:")
        print("1. 确保MySQL服务器已安装并正在运行")
        print("2. 检查主机地址是否正确")
        print("3. 如果使用的是远程MySQL服务器，检查网络连接")
        print("4. 尝试使用以下命令检查MySQL服务状态:")
        print("   systemctl status mysql  # 对于Linux")
        print("   或")
        print("   net start mysql  # 对于Windows")

成功连接到MySQL服务器
数据库 'target_db' 已存在，正在删除...
数据库 'target_db' 已成功删除
数据库 'target_db' 创建成功或已存在
切换到数据库 'target_db'

数据库操作完成，连接已关闭


In [22]:
import pymysql
import pandas as pd
import os

try:
    # 连接到MySQL服务器
    conn = pymysql.connect(
        host='localhost',
        user='newuser',
        password='Sict@2024',
        database='target_db',  # 直接指定数据库
        charset='utf8mb4'
    )
    print("成功连接到MySQL服务器")
    
    # 创建一个游标对象
    cursor = conn.cursor()
    
    # 查看数据库中的所有表
    cursor.execute("SHOW TABLES;")
    tables = cursor.fetchall()
    print("\n数据库中的表:")
    for table in tables:
        print(table[0])
    
    # 创建输出目录（如果不存在）
    output_dir = '/home/limeng/SICT/lung_test/csv_exports'
    os.makedirs(output_dir, exist_ok=True)
    
    # 为每个表导出CSV
    for table in tables:
        table_name = table[0]
        print(f"\n处理表: {table_name}")
        
        # 查看表结构
        cursor.execute(f"DESCRIBE {table_name};")
        columns = cursor.fetchall()
        print(f"表 {table_name} 结构:")
        for column in columns:
            print(f"列名: {column[0]}, 类型: {column[1]}, 可为空: {column[2]}, 键: {column[3]}, 默认值: {column[4]}, 额外信息: {column[5]}")
        
        # 查询数据
        cursor.execute(f"SELECT * FROM {table_name};")
        rows = cursor.fetchall()
        
        # 获取列名
        column_names = [column[0] for column in columns]
        
        # 创建DataFrame
        df = pd.DataFrame(rows, columns=column_names)
        
        # 打印数据预览
        print(f"\n表 {table_name} 数据预览:")
        print(df.head())
        
        # 导出为CSV
        csv_file_path = os.path.join(output_dir, f"{table_name}_data.csv")
        df.to_csv(csv_file_path, index=False, encoding='utf-8-sig')
        print(f"表 {table_name} 数据已导出到 {csv_file_path}")
    
    # 关闭数据库连接
    conn.close()
    print("\n数据库连接已关闭")
    print(f"所有表数据已导出到目录: {output_dir}")

except pymysql.Error as e:
    print(f"MySQL错误: {e}")

成功连接到MySQL服务器

数据库中的表:
coc_zy_hbzl_blbg
coc_zy_hbzl_blbg_qtsjlbj
coc_zy_hbzl_cyxj
coc_zy_hbzl_flxj
coc_zy_hbzl_flxj_fszljl
coc_zy_hbzl_hjbg
coc_zy_hbzl_mzbs
coc_zy_hbzl_mzmdtjl
coc_zy_hbzl_ryjl
coc_zy_hbzl_ryjl_grs
coc_zy_hbzl_ryjl_jws
coc_zy_hbzl_ryjl_sysyfzjc
coc_zy_hbzl_ryjl_tgjc
coc_zy_hbzl_ryjl_xbs
coc_zy_hbzl_ryjl_yjs
coc_zy_hbzl_ryjl_zkjc
coc_zy_hbzl_ryjlfl
coc_zy_hbzl_ryjlfl_fzjc
coc_zy_hbzl_ryjlfl_grs
coc_zy_hbzl_ryjlfl_jws
coc_zy_hbzl_ryjlfl_tgjc
coc_zy_hbzl_ryjlfl_xbs
coc_zy_hbzl_ryjlfl_xthg
coc_zy_hbzl_ryjlfl_zkjc
coc_zy_hbzl_scbcl
coc_zy_hbzl_sfjl
coc_zy_hbzl_ssjl
coc_zy_hbzl_yxbg
coc_zy_hbzl_zymdtjl

处理表: coc_zy_hbzl_blbg
表 coc_zy_hbzl_blbg 结构:
列名: id, 类型: bigint, 可为空: NO, 键: PRI, 默认值: None, 额外信息: auto_increment
列名: yljgdm, 类型: varchar(11), 可为空: NO, 键: , 默认值: None, 额外信息: 
列名: hzbh, 类型: varchar(32), 可为空: NO, 键: , 默认值: None, 额外信息: 
列名: jzlsh, 类型: varchar(32), 可为空: NO, 键: , 默认值: None, 额外信息: 
列名: jlsj, 类型: varchar(32), 可为空: YES, 键: , 默认值: None, 额外信息: 
列名: kh, 类型: varchar(32),

In [20]:
import pandas as pd
import re
import os

# 读取CSV文件
csv_path = '/home/limeng/SICT/lung_test/result/reflected_result319.csv'
df = pd.read_csv(csv_path, encoding='gb2312')

# 首先，从SQL文件中获取每个表的NOT NULL字段信息
sql_file_path = '/home/limeng/SICT/lung_test/喉癌.sql'

# 存储每个表的NOT NULL字段
current_table = None
table_not_null_fields = {}

# 逐行读取和处理文件
with open(sql_file_path, 'r', encoding='utf-8') as f:
    for line in f:
        line = line.strip()
        
        # 检查是否是CREATE TABLE行
        if line.startswith('CREATE TABLE'):
            # 提取表名
            table_match = line.split('`')[1] if '`' in line else line.split()[2]
            current_table = table_match.lower()
            table_not_null_fields[current_table] = []
        
        # 如果当前在处理表定义，且行中包含NOT NULL
        elif current_table and 'NOT NULL' in line:
            # 提取字段名
            if '`' in line:
                field_name = line.split('`')[1].lower()
                table_not_null_fields[current_table].append(field_name)

print(f"从SQL文件中找到 {len(table_not_null_fields)} 个表")
print(f"共找到 {sum(len(fields) for fields in table_not_null_fields.values())} 个NOT NULL字段")

# 按照groupby字段分组数据
grouped_data = {}
for index, row in df.iterrows():
    # 跳过没有规范节点名的行
    if pd.isna(row['规范节点名']):
        continue
    
    # 提取表名和字段名
    match = re.match(r'(COC_[^$]+)\$(.+)', row['规范节点名'])
    if not match:
        continue
    
    # 将表名和字段名转换为小写
    table_name = match.group(1).lower()
    field_name = match.group(2).lower()
    
    # 表名添加zy前缀
    formatted_table_name = table_name.replace('coc_', 'coc_zy_')
    
    # 获取分组键
    id_value = str(row['Id']) if 'Id' in df.columns and not pd.isna(row['Id']) else str(index)
    ipblh = str(row['IPBLH']) if not pd.isna(row['IPBLH']) else ''
    sfzh = str(row['SFZH']) if not pd.isna(row['SFZH']) else ''
    xgrq = str(row['XGRQ']) if not pd.isna(row['XGRQ']) else ''
    
    # 分组键使用表名和基本字段
    group_key = (formatted_table_name, id_value, ipblh, sfzh, xgrq)
    
    # 初始化分组数据
    if group_key not in grouped_data:
        grouped_data[group_key] = {}
    
    # 直接使用processed_string作为字段值
    processed_string = row['processed_string'] if not pd.isna(row['processed_string']) else ''
    
    # 如果字段是sswss_sss_sssj，截取前10个字符
    if field_name == 'sswss_sss_sssj':
        processed_string = processed_string[:10]
        print(f"字段 {field_name} 的值已截取为: {processed_string}")
    
    grouped_data[group_key][field_name] = processed_string

# 生成SQL插入语句
insert_sqls = []

for group_key, fields_data in grouped_data.items():
    formatted_table_name, id_value, ipblh, sfzh, xgrq = group_key
    
    if not fields_data:  # 跳过没有字段的表
        continue
    
    # 获取当前表的必填字段
    required_fields = []
    if formatted_table_name in table_not_null_fields:
        required_fields = table_not_null_fields[formatted_table_name]
    
    # 准备字段列表和值列表
    field_names = []
    values = []
    
    # 处理所有必填字段
    for field in required_fields:
        field_names.append(field)
        
        # 根据字段类型赋值
        if field == 'id':
            values.append(f"'{id_value}'")
        elif field == 'yljgdm':
            values.append("'42502658000'")
        elif field == 'hzbh':
            values.append(f"'{sfzh}'")  # hzbh对应SFZH
        elif field == 'jzlsh':
            values.append(f"'{ipblh}'")  # jzlsh对应IPBLH
        elif field == 'jlsj':
            values.append(f"'{xgrq}'")   # jlsj对应XGRQ
        elif field == 'kh':
            values.append("'01'")        # 默认科号
        elif field == 'klx':
            values.append("'1'")         # 默认科室类型
        elif field == 'xgbz':
            values.append("'1'")         # 修改标志统一为1
        elif field == 'yjlxh':
            values.append("'1'")         # 默认医疗流水号为1
        elif field in fields_data:
            # 如果数据中有该字段的值，则使用该值
            escaped_value = fields_data[field].replace("'", "''")
            values.append(f"'{escaped_value}'")
            # 从fields_data中移除已处理的字段，避免重复
            del fields_data[field]
        else:
            # 对于其他必填字段，提供一个默认空值
            values.append("''")
    
    # 添加其余非必填字段的值
    for field, value in fields_data.items():
        field_names.append(field)
        escaped_value = value.replace("'", "''")
        values.append(f"'{escaped_value}'")
    
    # 生成最终的INSERT语句
    field_list = ", ".join(field_names)
    value_list = ", ".join(values)
    
    insert_sql = f"INSERT INTO {formatted_table_name} ({field_list}) VALUES ({value_list});"
    insert_sqls.append(insert_sql)

# 将SQL语句写入文件
output_file = 'hegan_direct_inserts_required_fields.sql'
with open(output_file, 'w', encoding='utf-8') as f:
    for sql in insert_sqls:
        f.write(sql + '\n')

# 输出统计信息
print(f"\n已生成 {len(insert_sqls)} 条SQL插入语句")
print(f"SQL语句已保存到文件: {output_file}")

从SQL文件中找到 29 个表
共找到 168 个NOT NULL字段
字段 sswss_sss_sssj 的值已截取为: 2024/12/6 
字段 sswss_sss_sssj 的值已截取为: 2024/12/6 
字段 sswss_sss_sssj 的值已截取为: 2024/12/5 
字段 sswss_sss_sssj 的值已截取为: 2024/12/5 
字段 sswss_sss_sssj 的值已截取为: 2024/12/13
字段 sswss_sss_sssj 的值已截取为: 2024/12/13
字段 sswss_sss_sssj 的值已截取为: 2024/12/3 
字段 sswss_sss_sssj 的值已截取为: 2024/12/3 
字段 sswss_sss_sssj 的值已截取为: 2024/12/30
字段 sswss_sss_sssj 的值已截取为: 2024/12/30

已生成 34 条SQL插入语句
SQL语句已保存到文件: hegan_direct_inserts_required_fields.sql


In [23]:
import pymysql
import os

# 数据库连接配置
db_config = {
    'host': 'localhost',
    'user': 'newuser',
    'password': 'Sict@2024',
    'database': 'target_db',
    'charset': 'utf8mb4'
}

# SQL文件路径
sql_file_path = '/home/limeng/SICT/lung_test/hegan_direct_inserts_required_fields.sql'

try:
    # 连接到MySQL服务器
    conn = pymysql.connect(**db_config)
    print("成功连接到MySQL服务器")
    
    # 创建一个游标对象
    cursor = conn.cursor()
    
    # 读取SQL文件
    with open(sql_file_path, 'r', encoding='utf-8') as f:
        sql_statements = f.read().split(';')
    
    # 执行SQL语句
    success_count = 0
    error_count = 0
    
    for statement in sql_statements:
        # 跳过空语句
        if not statement.strip():
            continue
        
        try:
            # 执行SQL语句
            cursor.execute(statement)
            success_count += 1
            
            # 每100条语句提交一次，减少数据库负担
            if success_count % 100 == 0:
                conn.commit()
                print(f"已成功执行 {success_count} 条SQL语句")
                
        except pymysql.Error as e:
            error_count += 1
            print(f"执行SQL语句时出错: {e}")
            print(f"错误的SQL语句: {statement}")
    
    # 最后提交剩余的更改
    conn.commit()
    
    # 输出执行结果
    print("\n执行完成!")
    print(f"成功执行: {success_count} 条SQL语句")
    print(f"执行失败: {error_count} 条SQL语句")
    
    # 验证数据是否已插入
    for table_name in set([stmt.split()[2].lower() for stmt in sql_statements if stmt.strip().upper().startswith('INSERT')]):
        try:
            cursor.execute(f"SELECT COUNT(*) FROM {table_name}")
            count = cursor.fetchone()[0]
            print(f"表 {table_name} 现有 {count} 条记录")
        except pymysql.Error as e:
            print(f"查询表 {table_name} 记录数时出错: {e}")
    
    # 关闭数据库连接
    cursor.close()
    conn.close()
    print("\n数据库连接已关闭")

except pymysql.Error as e:
    print(f"MySQL连接错误: {e}")
except FileNotFoundError:
    print(f"SQL文件不存在: {sql_file_path}")
except Exception as e:
    print(f"发生错误: {e}")

成功连接到MySQL服务器

执行完成!
成功执行: 34 条SQL语句
执行失败: 0 条SQL语句
表 coc_zy_hbzl_ryjlfl_xbs 现有 1 条记录
表 coc_zy_hbzl_zymdtjl 现有 2 条记录
表 coc_zy_hbzl_ryjl_tgjc 现有 1 条记录
表 coc_zy_hbzl_scbcl 现有 1 条记录
表 coc_zy_hbzl_ryjlfl_tgjc 现有 1 条记录
表 coc_zy_hbzl_ryjl_yjs 现有 1 条记录
表 coc_zy_hbzl_ryjl_sysyfzjc 现有 1 条记录
表 coc_zy_hbzl_ssjl 现有 5 条记录
表 coc_zy_hbzl_mzmdtjl 现有 5 条记录
表 coc_zy_hbzl_cyxj 现有 2 条记录
表 coc_zy_hbzl_ryjl 现有 2 条记录
表 coc_zy_hbzl_ryjlfl_fzjc 现有 1 条记录
表 coc_zy_hbzl_ryjl_jws 现有 5 条记录
表 coc_zy_hbzl_ryjlfl 现有 6 条记录

数据库连接已关闭


In [13]:
import pymysql
import pandas as pd
import os

try:
    # 连接到MySQL服务器
    conn = pymysql.connect(
        host='localhost',
        user='newuser',
        password='Sict@2024',
        database='target_db',  # 直接指定数据库
        charset='utf8mb4'
    )
    print("成功连接到MySQL服务器")
    
    # 创建一个游标对象
    cursor = conn.cursor()
    
    # 查看数据库中的所有表
    cursor.execute("SHOW TABLES;")
    tables = cursor.fetchall()
    print("\n数据库中的表:")
    for table in tables:
        print(table[0])
    
    # 创建输出目录（如果不存在）
    output_dir = '/home/limeng/SICT/lung_test/csv_exports'
    os.makedirs(output_dir, exist_ok=True)
    
    # 为每个表导出CSV
    for table in tables:
        table_name = table[0]
        print(f"\n处理表: {table_name}")
        
        # 查看表结构
        cursor.execute(f"DESCRIBE {table_name};")
        columns = cursor.fetchall()
        print(f"表 {table_name} 结构:")
        for column in columns:
            print(f"列名: {column[0]}, 类型: {column[1]}, 可为空: {column[2]}, 键: {column[3]}, 默认值: {column[4]}, 额外信息: {column[5]}")
        
        # 查询数据
        cursor.execute(f"SELECT * FROM {table_name};")
        rows = cursor.fetchall()
        
        # 获取列名
        column_names = [column[0] for column in columns]
        
        # 创建DataFrame
        df = pd.DataFrame(rows, columns=column_names)
        
        # 打印数据预览
        print(f"\n表 {table_name} 数据预览:")
        print(df.head())
        
        # 导出为CSV
        csv_file_path = os.path.join(output_dir, f"{table_name}_data.csv")
        df.to_csv(csv_file_path, index=False, encoding='utf-8-sig')
        print(f"表 {table_name} 数据已导出到 {csv_file_path}")
    
    # 关闭数据库连接
    conn.close()
    print("\n数据库连接已关闭")
    print(f"所有表数据已导出到目录: {output_dir}")

except pymysql.Error as e:
    print(f"MySQL错误: {e}")

成功连接到MySQL服务器

数据库中的表:
coc_zy_hbzl_blbg
coc_zy_hbzl_blbg_qtsjlbj
coc_zy_hbzl_cyxj
coc_zy_hbzl_flxj
coc_zy_hbzl_flxj_fszljl
coc_zy_hbzl_hjbg
coc_zy_hbzl_mzbs
coc_zy_hbzl_mzmdtjl
coc_zy_hbzl_ryjl
coc_zy_hbzl_ryjl_grs
coc_zy_hbzl_ryjl_jws
coc_zy_hbzl_ryjl_sysyfzjc
coc_zy_hbzl_ryjl_tgjc
coc_zy_hbzl_ryjl_xbs
coc_zy_hbzl_ryjl_yjs
coc_zy_hbzl_ryjl_zkjc
coc_zy_hbzl_ryjlfl
coc_zy_hbzl_ryjlfl_fzjc
coc_zy_hbzl_ryjlfl_grs
coc_zy_hbzl_ryjlfl_jws
coc_zy_hbzl_ryjlfl_tgjc
coc_zy_hbzl_ryjlfl_xbs
coc_zy_hbzl_ryjlfl_xthg
coc_zy_hbzl_ryjlfl_zkjc
coc_zy_hbzl_scbcl
coc_zy_hbzl_sfjl
coc_zy_hbzl_ssjl
coc_zy_hbzl_yxbg
coc_zy_hbzl_zymdtjl

处理表: coc_zy_hbzl_blbg
表 coc_zy_hbzl_blbg 结构:
列名: id, 类型: bigint, 可为空: NO, 键: PRI, 默认值: None, 额外信息: auto_increment
列名: yljgdm, 类型: varchar(11), 可为空: YES, 键: , 默认值: None, 额外信息: 
列名: hzbh, 类型: varchar(32), 可为空: YES, 键: , 默认值: None, 额外信息: 
列名: jzlsh, 类型: varchar(32), 可为空: YES, 键: , 默认值: None, 额外信息: 
列名: jlsj, 类型: varchar(32), 可为空: YES, 键: , 默认值: None, 额外信息: 
列名: kh, 类型: varchar(3

In [ ]:
import pymysql
import pandas as pd
import os

try:
    # 连接到MySQL服务器
    conn = pymysql.connect(
        host='localhost',
        user='newuser',
        password='Sict@2024',
        database='target_db',  # 直接指定数据库
        charset='utf8mb4'
    )
    print("成功连接到MySQL服务器")
    
    # 创建一个游标对象
    cursor = conn.cursor()
    
    # 查看数据库中的所有表
    cursor.execute("SHOW TABLES;")
    tables = cursor.fetchall()
    print("\n数据库中的表:")
    for table in tables:
        print(table[0])
    
    # 创建输出目录（如果不存在）
    output_dir = '/home/limeng/SICT/lung_test/csv_exports'
    os.makedirs(output_dir, exist_ok=True)
    
    # 为每个表导出CSV
    for table in tables:
        table_name = table[0]
        print(f"\n处理表: {table_name}")
        
        # 查看表结构
        cursor.execute(f"DESCRIBE {table_name};")
        columns = cursor.fetchall()
        print(f"表 {table_name} 结构:")
        for column in columns:
            print(f"列名: {column[0]}, 类型: {column[1]}, 可为空: {column[2]}, 键: {column[3]}, 默认值: {column[4]}, 额外信息: {column[5]}")
        
        # 查询数据
        cursor.execute(f"SELECT * FROM {table_name};")
        rows = cursor.fetchall()
        
        # 获取列名
        column_names = [column[0] for column in columns]
        
        # 创建DataFrame
        df = pd.DataFrame(rows, columns=column_names)
        
        # 打印数据预览
        print(f"\n表 {table_name} 数据预览:")
        print(df.head())
        
        # 导出为CSV
        csv_file_path = os.path.join(output_dir, f"{table_name}_data.csv")
        df.to_csv(csv_file_path, index=False, encoding='utf-8-sig')
        print(f"表 {table_name} 数据已导出到 {csv_file_path}")
    
    # 关闭数据库连接
    conn.close()
    print("\n数据库连接已关闭")
    print(f"所有表数据已导出到目录: {output_dir}")

except pymysql.Error as e:
    print(f"MySQL错误: {e}")